# Random Forest Baseline Advanced Optimization 

Cloned from: [Feature_selection_LR_airlinejoin (baseline-3)](tobe update)
- Has the hyperparameter tuning for the baseline with all features for midterm.

- What is this notebook for? 
  - Notebook that runs the baseline Random Forest with advanced optimization
  - Machine Learning Algorithms : Random Forest
  - Metrics: F1, accuracy, precision
  
---
  
- Data:
  - Final, cleaned weather
  - Cleaned flights minus (PR departure delay, PR arrival delay, carrier ordinal)

RF in spark

https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/1898361324232092/command/1898361324232093

Feature selection in RF

https://antonhaugen.medium.com/feature-selection-for-pyspark-tree-classifiers-3be54a8bc493

# 0. Preparation

In [0]:
import pandas as pd
import numpy as np
import os
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
import ast
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import geopandas as gpd
import folium
import time
import hyperopt

from pyspark.sql.functions import col, max, min
from pyspark.sql.functions import col,isnan,when,count
from pyspark.sql.functions import desc
from pyspark.sql.types import DateType
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler
from pyspark.ml.feature import MinMaxScaler
from pyspark.mllib.evaluation import MulticlassMetrics, BinaryClassificationMetrics
from pyspark.ml.evaluation import BinaryraClassificationEvaluator
from pyspark.sql.functions import add_months, date_add
from pyspark.ml.classification import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV

from hyperopt import tpe, hp, fmin, STATUS_OK
from hyperopt.pyll.base import scope

from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
from hyperopt import Trials



In [0]:
# !pip install hyperopt
!/databricks/python3/bin/python -m pip install --upgrade pip
!pip install hyperopt
!pip install folium

Requirement already satisfied: pip in /databricks/python3/lib/python3.8/site-packages (22.0.4)
Requirement already satisfied: hyperopt in /databricks/python3/lib/python3.8/site-packages (0.2.7)
Requirement already satisfied: six in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (1.15.0)
Requirement already satisfied: py4j in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (0.10.9.5)
Requirement already satisfied: tqdm in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (4.59.0)
Requirement already satisfied: numpy in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (1.19.2)
Requirement already satisfied: scipy in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (1.6.2)
Requirement already satisfied: networkx>=2.2 in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (2.5)
Requirement already satisfied: cloudpickle in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (1.6.0)
Requirement already satisfied: future in /databricks/python3/lib/python3.8/site-packages (from hyperopt) (0.18.2)
Requirement already satisfied: decorator>=4.3.0 in /databricks/python3/lib/python3.8/site-packages (from networkx>=2.2->hyperopt) (5.0.6)

In [0]:
# Put at the top of any notebooks for storing in blob

from pyspark.sql.functions import col, max

blob_container = "team06" # The name of your container created in https://portal.azure.com
storage_account = "apatel" # The name of your Storage account created in https://portal.azure.com
secret_scope = "team06" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "team06" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

## Import fully joined data

In [0]:
df_5yr_join = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_depPR_arrPR_v3')



# IMPORTANT: update full data to v8

In [0]:
# Added April 6 with new features
# df_5yr_join_april6 = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_extraFeatures_v4_4-6-22')

df_5yr_join_april7 = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_extraFeatures_upToOD_good_v8_4-6-22')

In [0]:
df_5yr_join_april7.columns

Out[37]: ['YEAR',
 'QUARTER',
 'MONTH',
 'DAY_OF_MONTH',
 'DAY_OF_WEEK',
 'FL_DATE',
 'OP_UNIQUE_CARRIER',
 'OP_CARRIER_AIRLINE_ID',
 'TAIL_NUM',
 'OP_CARRIER_FL_NUM',
 'ORIGIN_AIRPORT_ID',
 'ORIGIN_AIRPORT_SEQ_ID',
 'ORIGIN',
 'ORIGIN_STATE_ABR',
 'ORIGIN_STATE_FIPS',
 'ORIGIN_STATE_NM',
 'DEST_AIRPORT_ID',
 'DEST_AIRPORT_SEQ_ID',
 'DEST',
 'DEST_STATE_ABR',
 'DEST_STATE_FIPS',
 'DEST_STATE_NM',
 'CRS_DEP_TIME',
 'DEP_TIME',
 'DEP_DELAY',
 'DEP_DELAY_NEW',
 'DEP_DEL15',
 'DEP_DELAY_GROUP',
 'DEP_TIME_BLK',
 'CRS_ARR_TIME',
 'ARR_TIME',
 'ARR_DELAY',
 'ARR_DELAY_NEW',
 'ARR_DEL15',
 'CANCELLED',
 'ACTUAL_ELAPSED_TIME',
 'DISTANCE',
 'DISTANCE_GROUP',
 'CARRIER_DELAY',
 'WEATHER_DELAY',
 'NAS_DELAY',
 'LATE_AIRCRAFT_DELAY',
 'ORI_IATA',
 'ORI_station_id',
 'ORI_station_lat',
 'ORI_station_lon',
 'ORI_airport_lat',
 'ORI_airport_lon',
 'ORI_elevation',
 'ORI_dist_airp_sta',
 'DEST_IATA',
 'DEST_station_id',
 'DEST_station_lat',
 'DEST_station_lon',
 'DEST_airport_lat',
 'DEST_airport_lon',
 'DEST_elevation',
 'DEST_dist_airp_sta',
 'CRS_DEP_HRS',
 'CRS_DEP_MINS',
 'CRS_DEP_TIME_STR',
 'CRS_DEP_DT_STR',
 'CRS_DEP_DATETIME',
 'iata_code',
 'ORI_timezone',
 'CRS_DEP_DATETIME_UTC',
 'CRS_DEP_DATETIME_UTC_END',
 'CRS_DEP_DATETIME_UTC_START',
 'STATION',
 'DATE',
 'LATITUDE',
 'LONGITUDE',
 'ELEVATION',
 'REPORT_TYPE',
 'DEST_timezone',
 'DEP_HRS',
 'DEP_MINS',
 'DEP_TIME_STR',
 'DEP_DT_STR',
 'DEP_DATETIME',
 'ARR_DATETIME_ACTUAL_UTC',
 'late_night',
 'daytime',
 'evening',
 'region_name',
 'new_england',
 'mid_atlantic',
 'south',
 'midwest',
 'southwest',
 'west',
 'pacific_islands',
 'atlantic_islands',
 'spring',
 'summer',
 'autumn',
 'winter',
 'dep_date',
 'weekend_or_holiday',
 'flightID',
 'ID',
 'previous_flight_delay_status',
 'previous_flight_dep_time',
 'time_between_departures_min',
 'valid_dep_delay',
 'prior_dep_delayed',
 'previous_DEP_DELAY_NEW_value',
 'previous_DEP_DELAY_NEW',
 'previous_flight_arrdelay_status',
 'previous_flight_arr_time',
 'time_between_arrival_and_end_min',
 'valid_arr_delay',
 'prior_arr_delayed',
 'previous_ARR_DELAY_NEW_value',
 'previous_ARR_DELAY_NEW',
 'prev_arrival_airport',
 'plane_is_here',
 'avg_carrier_delay_24hrs',
 'flights_sch_Today_ORIGIN',
 'flights_sch_Today_DEST',
 'avg_ori_airport_delay_24hrs',
 'year_quarter',
 'quarter_enum',
 'quarter_enum_prev',
 'month_seq_index',
 'wnd_2_wind_obs_type',
 'wnd_3_wind_sp_rate',
 'cig_0_height',
 'vis_0_distance',
 'slp_0_day_avg',
 'tmp_0_air_temp',
 'dew_0_point_temp',
 'ma1_0_altimeter_setting_rate',
 'ma1_2_station_pressure_rate',
 'gd1_3_sky_cover_height',
 'WND_3_wind_speed',
 'CIG_0_sky_ceiling_height',
 'VIS_0_visibility_dist',
 'SLP_0_avg_station_press',
 'TMP_0_air_temperature',
 'DEW_0_dew_pt_temp',
 'MA1_0_altimeter_set_rate',
 'MA1_2_station_pres_rate',
 'OC1_0_wind_gust_spd_rate_imp',
 'GD1_3_cloud_height',
 'AA1_1_liquid_precip',
 'AA3_1_liquid_precip',
 'gd1_0_sky_coverage',
 'au2_4_extreme_wind_weather',
 'mv1_0_sand_dust_near',
 'mv1_0_thunder_rain_near',
 'aw1_mw1_0_smoke_haze_dust',
 'aw1_mw1_0_fog',
 'aw1_mw1_0_rain_drizzle',
 'aw1_mw1_0_freezing_rain_drizzle',
 'aw1_mw1_0_snow',
 'aw1_mw1_0_hail_or_ice',
 'aw1_mw1_0_thunderstorm',
 'aw1_mw1_0_tornado',
 'SLP_0_avg_station_press_imp',
 'WND_3_wind_speed_imp',
 'CIG_0_sky_ceiling_height_imp',
 'VIS_0_visibility_dist_imp',
 'TMP_0_air_temperature_imp',
 'DEW_0_dew_pt_temp_imp',
 'MA1_0_altimeter_set_rate_imp',
 'MA1_2_station_pres_rate_imp',
 'GD1_3_cloud_height_imp',
 'depDelayPageRank',
 'arrDelayPageRank',
 'UniqueID',
 'hour',
 'hour_UTC',
 'avg_hourly_delay_24hr',
 'OD_Pair',
 'avg_OD_dep_del15_24hr',
 'avg_OD_delay_min_24hr',
 'avg_OD_num_flights_24hr',
 'depDelayPageRank_ordinal',
 'arrDelayPageRank_ordinal',
 'recent_dep_time',
 'recent_dep_dest',
 'time_between_currentDepTime_recentDepTime',
 'dep_flight_after_prediction',
 'recent_dep_flight_coming_here',
 'departed_for_current_aiport',
 '1st_most_recent_dep_UTC',
 '2nd_most_recent_dep_UTC',
 '1st_most_recent_a

In [0]:
# copied from section `Flights Features to Keep`
features_for_flights=[ 'DISTANCE','ORI_elevation','DEST_elevation', 
                   'prior_dep_delayed', 'previous_DEP_DELAY_NEW',
                    'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here',
                    'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs',
                    'daytime', 'evening',
                    'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands',
                    'summer', 'winter', 'autumn',
                    'weekend_or_holiday']

# extra_features_added_april6 = ['avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr']

# added on april6 + april7
extra_features_added_april7 = ['avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

# one-hot encoded variables should be n-1. Eliminate one of the one-hot encoded categoricals to the all 0 case represents it.
# Dropped: 'late_night', 'new_england', 'spring'


features_for_weathers=['OC1_0_wind_gust_spd_rate_imp','AA1_1_liquid_precip','AA3_1_liquid_precip','gd1_0_sky_coverage',
                       'au2_4_extreme_wind_weather','mv1_0_sand_dust_near','mv1_0_thunder_rain_near','aw1_mw1_0_smoke_haze_dust','aw1_mw1_0_fog',
                       'aw1_mw1_0_rain_drizzle','aw1_mw1_0_freezing_rain_drizzle','aw1_mw1_0_snow','aw1_mw1_0_hail_or_ice','aw1_mw1_0_thunderstorm',
                       'aw1_mw1_0_tornado','SLP_0_avg_station_press_imp','WND_3_wind_speed_imp','CIG_0_sky_ceiling_height_imp',
                       'VIS_0_visibility_dist_imp','TMP_0_air_temperature_imp','DEW_0_dew_pt_temp_imp','MA1_0_altimeter_set_rate_imp',
                       'MA1_2_station_pres_rate_imp','GD1_3_cloud_height_imp']

features_for_pagerank = ['depDelayPageRank', 'arrDelayPageRank']

# Original total features
feature_list_full_0 = features_for_flights + features_for_weathers + features_for_pagerank


feature_list_full = ['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado'] + ['depDelayPageRank', 'arrDelayPageRank']

# old ten selected features(comment out)
# feature_list = ['prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'evening', 'previous_ARR_DELAY_NEW', 
#                 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs',
#                'depDelayPageRank', 'arrDelayPageRank']


# specify any outcome variables you also want to check for missing
outcomes_for_flights=['DEP_DEL15']#, 'DEP_DELAY_NEW']

# combine:
model_col_list = outcomes_for_flights + feature_list_full_0
model_col_list_april7 = outcomes_for_flights + feature_list_full_0 + extra_features_added_april7

print(model_col_list)

['DEP_DEL15', 'DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
features_for_cv = ['DATE'] + outcomes_for_flights + feature_list_full_0
features_for_cv_april7 =  ['DATE'] + outcomes_for_flights + feature_list_full_0 + extra_features_added_april7

print(features_for_cv_april7)

['DATE', 'DEP_DEL15', 'DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

In [0]:
features_list =  feature_list_full_0 + extra_features_added_april7

In [0]:
display(df_5yr_join_april7)

In [0]:
# null check
def displayMissingInDF(flights_df, cols_to_check = None):
  # train0_null_check = train0.drop("CRS_DEP_DATETIME_UTC_END")
  if type(cols_to_check)==list:
    pass
  else:
    cols_to_check = flights_df.columns
  null_cnt_df = flights_df.select([count(when(col(c).contains('None') | \
                            col(c).contains('NULL') | \
                            (col(c) == '' ) | \
                            col(c).isNull() | \
                            isnan(c), c 
                           )).alias(c)
                    for c in cols_to_check])

  display(null_cnt_df)

## Select features for CV split and modeling

In [0]:
df_5yr_join_cv = df_5yr_join.select(features_for_cv)
df_5yr_join_cv_april7 = df_5yr_join_april7.select(features_for_cv_april7)

df_5yr_join_cv =df_5yr_join_cv.cache()
df_5yr_join_cv_april7 = df_5yr_join_cv_april7.cache()

In [0]:
# displayMissingInDF(df_5yr_join_cv, model_col_list)

In [0]:
# displayMissingInDF(df_5yr_join_cv_april7, model_col_list_april7)

In [0]:
print(f"Number of rows in dataset pre-split: df_5yr_join_cv {df_5yr_join_cv.count()}")
print(f"Number of rows in dataset pre-split: df_5yr_join_cv_april7 {df_5yr_join_cv_april7.count()}")

# 2. Train/ Hold-out/ Test split *Custom CV added

- Create a custom cross validation split
- Hold-out data always comes later than train data and test data comes later than all the train/ hold-out data

## 2.0 Conduct Block Time Series Split (5 years)
CV diagram for the entire dataset:

![CV for Full Data](files/shared_uploads/anand.patel@berkeley.edu/CV_full_data.PNG)

|      | Train                    | Hold-out                 | Test                |
|------|--------------------------|--------------------------|---------------------|
| 1    | 2015-01-01 to 2015-06-30 | 2015-07-01 to 2015-08-31 | -                   |
| 2    | 2015-06-01 to 2015-11-30 | 2015-12-01 to 2016-01-31 | -                   |
| 3    | 2015-11-01 to 2016-04-30 | 2016-05-01 to 2016-06-30 | -                   |
| 4    | 2016-04-01 to 2016-09-30 | 2016-10-01 to 2016-11-30 | -                   |
| 5    | 2016-09-01 to 2017-02-28 | 2017-03-01 to 2016-04-30 | -                   |
| 6    | 2017-02-01 to 2017-07-31 | 2017-08-01 to 2017-09-30 | -                   |
| 7    | 2017-07-01 to 2018-12-31 | 2017-02-01 to 2017-02-28 | -                   |
| 8    | 2017-12-01 to 2018-05-30 | 2018-06-01 to 2018-07-31 | -                   |
| 9    | 2018-05-01 to 2018-10-31 | 2018-11-01 to 2018-12-31 |                     |
| Test | -                        | -                        | 2019-01-01 to end   |

In [0]:
# save out the data with just these columns.
# df_5yr_join_cv.write.parquet(f"{blob_url}/flights_all_feats_and_imputed_weather_v4_29")

In [0]:
print(f'features_for_cv: {len(features_for_cv)}, {features_for_cv}')
print(f'features_for_cv_april7: {len(features_for_cv_april7)}, {features_for_cv_april7}')

## 2-1 Custom Cross Validation split

Custom CV diagram for the entire dataset:

![Custom Cross Validation](files/shared_uploads/ruminakagawa@berkeley.edu/Screen_Shot_2022_04_06_at_16_09_51.png)

|      | Train                    | Hold-out                 | Test                |
|------|--------------------------|--------------------------|---------------------|
| 1    | 2015-01-01 to 2015-12-31 | 2016-01-01 to 2016-12-31 | -                   |
| 2    | 2016-01-01 to 2016-12-31 | 2017-01-01 to 2017-12-31 | -                   |
| 3    | 2017-01-01 to 2017-12-31 | 2018-01-01 to 2018-12-31 | -                   |
| 4    | 2017-07-01 to 2018-06-30 | 2018-07-01 to 2018-12-31 | -                   |
| 5    | 2016-07-01 to 2017-06-30 | 2017-07-01 to 2018-06-30 | -                   |
| Test | -                        | -                        | 2019-01-01 to end   |

### Custom CV split with existing dataset: df_5yr_join_cv

In [0]:
# dataset : df_5yr_join_cv
features_list =  feature_list_full_0 # + extra_features_added_april7
features_for_cv = features_for_cv#_april7

In [0]:
# Data split for 5-year CV is calcutated by the latest date

# name latest record as "latest_record"
df_CV_date = df_5yr_join_cv.select(max("DATE")).withColumnRenamed("max(DATE)","latest_record")
# name the start date of test data as test_start

df_CV_date = df_CV_date.withColumn("test_start_", add_months("latest_record",-12))
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("test_start", date_add("test_start_",+1))


# start date of cv group1: train0
df_CV_date = df_CV_date.withColumn("train0_custom_", add_months("latest_record",-60)).cache()
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("train0_custom", date_add("train0_custom_",+1))


# same as group1, calculate group2 to 8
df_CV_date = df_CV_date.withColumn("train1_custom", add_months("train0_custom",+12))
df_CV_date = df_CV_date.withColumn("train2_custom", add_months("train0_custom",+24))
df_CV_date = df_CV_date.withColumn("train3_custom", add_months("train0_custom",+30))
df_CV_date = df_CV_date.withColumn("train4_custom", add_months("train0_custom",+18))

# start date of cv group1: holdout0
df_CV_date = df_CV_date.withColumn("holdout0_custom", add_months("train0_custom",+12))
df_CV_date = df_CV_date.withColumn("holdout1_custom", add_months("holdout0_custom",+12))
df_CV_date = df_CV_date.withColumn("holdout2_custom", add_months("holdout0_custom",+24))
df_CV_date = df_CV_date.withColumn("holdout3_custom", add_months("holdout0_custom",+30))
df_CV_date = df_CV_date.withColumn("holdout4_custom", add_months("holdout0_custom",+18))

display(df_CV_date)

# use pandas because operation is much lighter
pdf_CV_date = df_CV_date.cache().toPandas()
print(pdf_CV_date)

# list of name of the dataset
cv_group_list = [['train0_custom','holdout0_custom'],['train1_custom','holdout1_custom'],['train2_custom','holdout2_custom'],
                 ['train3_custom','holdout3_custom'],['train4_custom','holdout4_custom']]


def CustomCVSplit_full(df, cv_group, feature_list):
  
  global pdf_CV_date#df_CV_date
  
  # assign start date
  train_start_date = pdf_CV_date[cv_group[0]][0]
  holdout_start_date = pdf_CV_date[cv_group[1]][0]
  print(f'{cv_group[0]}_start: {train_start_date}, {cv_group[1]}_start: {holdout_start_date}')

  # calculate end date of train/holdout data
  pdf_CV_date[cv_group[0]+'_end'] = train_start_date + relativedelta(months=+12)
  if cv_group[1] != 'holdout3_custom':
    pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+12)
  elif cv_group[1] == 'holdout3_custom':
    pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+6)
  
  # calculate end date of train/holdout data
  train_end_date = train_start_date + relativedelta(months=+12) - timedelta(days=1)
  if cv_group[1] != 'holdout3_custom':
    holdout_end_date = holdout_start_date + relativedelta(months=+12) - timedelta(days=1)
    print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
  elif cv_group[1] == 'holdout3_custom':
    holdout_end_date = holdout_start_date + relativedelta(months=+6) - timedelta(days=1)
    print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
  
  # train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= train_start_date) & (df_5yr_join_cv.DATE <= train_end_date))
  # holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= holdout_start_date) & (df_5yr_join_cv.DATE <= holdout_end_date))
  train = df.filter((df.DATE >= train_start_date) & (df.DATE <= train_end_date))
  holdout = df.filter((df.DATE >= holdout_start_date) & (df.DATE <= holdout_end_date))
  
  train = train.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  holdout = holdout.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  
  print(f"flights in {cv_group[0]}: {train.count()}, flights in {cv_group[1]}: {holdout.count()}")
  
  return train, holdout

train0_custom, holdout0_custom = CustomCVSplit_full(df_5yr_join_cv, cv_group_list[0], features_for_cv)
train1_custom, holdout1_custom = CustomCVSplit_full(df_5yr_join_cv, cv_group_list[1], features_for_cv)
train2_custom, holdout2_custom = CustomCVSplit_full(df_5yr_join_cv, cv_group_list[2], features_for_cv)
train3_custom, holdout3_custom = CustomCVSplit_full(df_5yr_join_cv, cv_group_list[3], features_for_cv)
train4_custom, holdout4_custom = CustomCVSplit_full(df_5yr_join_cv, cv_group_list[4], features_for_cv)

# have date column to check if the date is splitted correctly
test = df_5yr_join_cv.filter(df_5yr_join_cv.DATE >= df_CV_date.collect()[0]['test_start']).select(features_for_cv)# + ['DATE'])
trainAll = df_5yr_join_cv.filter(df_5yr_join_cv.DATE < df_CV_date.collect()[0]['test_start']).select(features_for_cv)# + ['DATE'])

print(f'test_start: ')
df_CV_date.collect()[0]['test_start']


###  CV split with extra features as of April 7: df_5yr_join_cv_april7

In [0]:
# dataset : df_5yr_join_cv_april7
features_list =  feature_list_full_0 + extra_features_added_april7
features_for_cv = features_for_cv_april7

In [0]:
# Data split for 5-year CV is calcutated by the latest date

# name latest record as "latest_record"
df_CV_date = df_5yr_join_cv_april7.select(max("DATE")).withColumnRenamed("max(DATE)","latest_record")
# name the start date of test data as test_start

df_CV_date = df_CV_date.withColumn("test_start_", add_months("latest_record",-12))
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("test_start", date_add("test_start_",+1))


# start date of cv group1: train0
df_CV_date = df_CV_date.withColumn("train0_custom_", add_months("latest_record",-60)).cache()
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("train0_custom", date_add("train0_custom_",+1))


# same as group1, calculate group2 to 8
df_CV_date = df_CV_date.withColumn("train1_custom", add_months("train0_custom",+12))
df_CV_date = df_CV_date.withColumn("train2_custom", add_months("train0_custom",+24))
df_CV_date = df_CV_date.withColumn("train3_custom", add_months("train0_custom",+30))
df_CV_date = df_CV_date.withColumn("train4_custom", add_months("train0_custom",+18))

# start date of cv group1: holdout0
df_CV_date = df_CV_date.withColumn("holdout0_custom", add_months("train0_custom",+12))
df_CV_date = df_CV_date.withColumn("holdout1_custom", add_months("holdout0_custom",+12))
df_CV_date = df_CV_date.withColumn("holdout2_custom", add_months("holdout0_custom",+24))
df_CV_date = df_CV_date.withColumn("holdout3_custom", add_months("holdout0_custom",+30))
df_CV_date = df_CV_date.withColumn("holdout4_custom", add_months("holdout0_custom",+18))

display(df_CV_date)

# use pandas because operation is much lighter
pdf_CV_date = df_CV_date.cache().toPandas()
print(pdf_CV_date)

# list of name of the dataset
cv_group_list = [['train0_custom','holdout0_custom'],['train1_custom','holdout1_custom'],['train2_custom','holdout2_custom'],
                 ['train3_custom','holdout3_custom'],['train4_custom','holdout4_custom']]


def CustomCVSplit_full(df, cv_group, feature_list):
  
  global pdf_CV_date#df_CV_date
  
  # assign start date
  train_start_date = pdf_CV_date[cv_group[0]][0]
  holdout_start_date = pdf_CV_date[cv_group[1]][0]
  print(f'{cv_group[0]}_start: {train_start_date}, {cv_group[1]}_start: {holdout_start_date}')

  # calculate end date of train/holdout data
  pdf_CV_date[cv_group[0]+'_end'] = train_start_date + relativedelta(months=+12)
  if cv_group[1] != 'holdout3_custom':
    pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+12)
  elif cv_group[1] == 'holdout3_custom':
    pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+6)
  
  # calculate end date of train/holdout data
  train_end_date = train_start_date + relativedelta(months=+12) - timedelta(days=1)
  if cv_group[1] != 'holdout3_custom':
    holdout_end_date = holdout_start_date + relativedelta(months=+12) - timedelta(days=1)
    print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
  elif cv_group[1] == 'holdout3_custom':
    holdout_end_date = holdout_start_date + relativedelta(months=+6) - timedelta(days=1)
    print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
  
  # train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= train_start_date) & (df_5yr_join_cv.DATE <= train_end_date))
  # holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= holdout_start_date) & (df_5yr_join_cv.DATE <= holdout_end_date))
  train = df.filter((df.DATE >= train_start_date) & (df.DATE <= train_end_date))
  holdout = df.filter((df.DATE >= holdout_start_date) & (df.DATE <= holdout_end_date))
  
  train = train.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  holdout = holdout.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  
  print(f"flights in {cv_group[0]}: {train.count()}, flights in {cv_group[1]}: {holdout.count()}")
  
  return train, holdout

train0_custom_april7, holdout0_custom_april7 = CustomCVSplit_full(df_5yr_join_cv_april7, cv_group_list[0], features_for_cv_april7)
train1_custom_april7, holdout1_custom_april7 = CustomCVSplit_full(df_5yr_join_cv_april7, cv_group_list[1], features_for_cv_april7)
train2_custom_april7, holdout2_custom_april7 = CustomCVSplit_full(df_5yr_join_cv_april7, cv_group_list[2], features_for_cv_april7)
train3_custom_april7, holdout3_custom_april7 = CustomCVSplit_full(df_5yr_join_cv_april7, cv_group_list[3], features_for_cv_april7)
train4_custom_april7, holdout4_custom_april7 = CustomCVSplit_full(df_5yr_join_cv_april7, cv_group_list[4], features_for_cv_april7)

# have date column to check if the date is splitted correctly
test_april7 = df_5yr_join_cv_april7.filter(df_5yr_join_cv_april7.DATE >= df_CV_date.collect()[0]['test_start']).select(features_for_cv_april7)# + ['DATE'])
trainAll_april7 = df_5yr_join_cv_april7.filter(df_5yr_join_cv_april7.DATE < df_CV_date.collect()[0]['test_start']).select(features_for_cv_april7)# + ['DATE'])

print(f'test_start: ')
df_CV_date.collect()[0]['test_start']


latest_record test_start_ test_start train0_custom_ train0_custom train1_custom train2_custom train3_custom train4_custom holdout0_custom holdout1_custom holdout2_custom holdout3_custom holdout4_custom 2019-12-31T23:57:00.000+0000 2018-12-31 2019-01-01 2014-12-31 2015-01-01 2016-01-01 2017-01-01 2017-07-01 2016-07-01 2016-01-01 2017-01-01 2018-01-01 2018-07-01 2017-07-01

latest_record test_start_ ... holdout3_custom holdout4_custom
0 2019-12-31 23:57:00 2018-12-31 ... 2018-07-01 2017-07-01

[1 rows x 14 columns]
train0_custom_start: 2015-01-01, holdout0_custom_start: 2016-01-01
train0_custom_end: 2015-12-31, holdout0_custom_end: 2016-12-31
flights in train0_custom: 5679843, flights in holdout0_custom: 5503535
train1_custom_start: 2016-01-01, holdout1_custom_start: 2017-01-01
train1_custom_end: 2016-12-31, holdout1_custom_end: 2017-12-31
flights in train1_custom: 5503535, flights in holdout1_custom: 5546936
train2_custom_start: 2017-01-01, holdout2_custom_start: 2018-01-01
train2_custom_end: 2017-12-31, holdout2_custom_end: 2018-12-31
flights in train2_custom: 5546936, flights in holdout2_custom: 7042669
train3_custom_start: 2017-07-01, holdout3_custom_start: 2018-07-01
train3_custom_end: 2018-06-30, holdout3_custom_end: 2018-12-31
flights in train3_custom: 6257716, flights in holdout3_custom: 3587815
train4_custom_start: 2016-07-01, holdout4_custom_start: 2017-07-01
train4_custom_end: 2017-06-30, holdout4_custom_end: 2018-06-30
flights in train4_custom: 5514687, flights in holdout4_custom: 6257716
test_start: 
Out[44]: datetime.date(2019, 1, 1)

## Basic CV split

In [0]:
# # Data split for 5-year CV is calcutated by the latest date

# # name latest record as "latest_record"
# df_CV_date = df_5yr_join_cv.select(max("DATE")).withColumnRenamed("max(DATE)","latest_record")
# # name the start date of test data as test_start

# df_CV_date = df_CV_date.withColumn("test_start_", add_months("latest_record",-12))
# # the line is unnecessary added because 20200101 is cut
# df_CV_date = df_CV_date.withColumn("test_start", date_add("test_start_",+1))


# # start date of cv group1: train0
# df_CV_date = df_CV_date.withColumn("train0_", add_months("latest_record",-60)).cache()
# # the line is unnecessary added because 20200101 is cut
# df_CV_date = df_CV_date.withColumn("train0", date_add("train0_",+1))


# # same as group1, calculate group2 to 8
# df_CV_date = df_CV_date.withColumn("train1", add_months("train0",+5))
# df_CV_date = df_CV_date.withColumn("train2", add_months("train0",+10))
# df_CV_date = df_CV_date.withColumn("train3", add_months("train0",+15))
# df_CV_date = df_CV_date.withColumn("train4", add_months("train0",+20))
# df_CV_date = df_CV_date.withColumn("train5", add_months("train0",+25))
# df_CV_date = df_CV_date.withColumn("train6", add_months("train0",+30))
# df_CV_date = df_CV_date.withColumn("train7", add_months("train0",+35))
# df_CV_date = df_CV_date.withColumn("train8", add_months("train0",+40))

# # start date of cv group1: holdout0
# df_CV_date = df_CV_date.withColumn("holdout0", add_months("train0",+6))
# df_CV_date = df_CV_date.withColumn("holdout1", add_months("holdout0",+5))
# df_CV_date = df_CV_date.withColumn("holdout2", add_months("holdout0",+10))
# df_CV_date = df_CV_date.withColumn("holdout3", add_months("holdout0",+15))
# df_CV_date = df_CV_date.withColumn("holdout4", add_months("holdout0",+20))
# df_CV_date = df_CV_date.withColumn("holdout5", add_months("holdout0",+25))
# df_CV_date = df_CV_date.withColumn("holdout6", add_months("holdout0",+30))
# df_CV_date = df_CV_date.withColumn("holdout7", add_months("holdout0",+35))
# df_CV_date = df_CV_date.withColumn("holdout8", add_months("holdout0",+40))

# display(df_CV_date)

# # use pandas because operation is much lighter
# pdf_CV_date = df_CV_date.cache().toPandas()
# print(pdf_CV_date)

# # list of name of the dataset
# cv_group_list = [['train0','holdout0'],['train1','holdout1'],['train2','holdout2'],
#                  ['train3','holdout3'],['train4','holdout4'],['train5','holdout5'],
#                  ['train6','holdout6'],['train7','holdout7'],['train8','holdout8']]


# def CVSplit_full1(df, cv_group, feature_list):
  
#   global pdf_CV_date#df_CV_date
  
#   # assign start date
#   train_start_date = pdf_CV_date[cv_group[0]][0]
#   holdout_start_date = pdf_CV_date[cv_group[1]][0]
#   print(f'{cv_group[0]}_start: {train_start_date}, {cv_group[1]}_start: {holdout_start_date}')

#   # calculate end date of train/holdout data
#   pdf_CV_date[cv_group[0]+'_end'] = train_start_date + relativedelta(months=+5)
#   pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+2)
  
#   # calculate end date of train/holdout data
#   train_end_date = train_start_date + relativedelta(months=+6) - timedelta(days=1)
#   holdout_end_date = holdout_start_date + relativedelta(months=+2) - timedelta(days=1)
#   print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
    
#   # train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= train_start_date) & (df_5yr_join_cv.DATE <= train_end_date))
#   # holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= holdout_start_date) & (df_5yr_join_cv.DATE <= holdout_end_date))
#   train = df.filter((df.DATE >= train_start_date) & (df.DATE <= train_end_date))
#   holdout = df.filter((df.DATE >= holdout_start_date) & (df.DATE <= holdout_end_date))
  
#   train = train.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
#   holdout = holdout.select(features_for_cv).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  
#   # If we want to split to X and Y, use the code below
#   #   train_X = train.select(feature_list)
#   #   train_Y = train.select(['DEP_DEL15'])
#   #   holdout_X = holdout.select(feature_list)
#   #   holdout_Y = holdout.select(['DEP_DEL15'])
  
#   print(f"flights in {cv_group[0]}: {train.count()}, flights in {cv_group[1]}: {holdout.count()}")
  
#   return train, holdout

# train0, holdout0 = CVSplit_full1(df_5yr_join_cv, cv_group_list[0], features_for_cv)
# train1, holdout1 = CVSplit_full1(df_5yr_join_cv, cv_group_list[1], features_for_cv)
# train2, holdout2 = CVSplit_full1(df_5yr_join_cv, cv_group_list[2], features_for_cv)
# train3, holdout3 = CVSplit_full1(df_5yr_join_cv, cv_group_list[3], features_for_cv)
# train4, holdout4 = CVSplit_full1(df_5yr_join_cv, cv_group_list[4], features_for_cv)
# train5, holdout5 = CVSplit_full1(df_5yr_join_cv, cv_group_list[5], features_for_cv)
# train6, holdout6 = CVSplit_full1(df_5yr_join_cv, cv_group_list[6], features_for_cv)
# train7, holdout7 = CVSplit_full1(df_5yr_join_cv, cv_group_list[7], features_for_cv)
# train8, holdout8 = CVSplit_full1(df_5yr_join_cv, cv_group_list[8], features_for_cv)

# # have date column to check if the date is splitted correctly
# test = df_5yr_join_cv.filter(df_5yr_join_cv.DATE >= df_CV_date.collect()[0]['test_start']).select(features_for_cv)# + ['DATE'])
# trainAll = df_5yr_join_cv.filter(df_5yr_join_cv.DATE < df_CV_date.collect()[0]['test_start']).select(features_for_cv)# + ['DATE'])

# print(f'test_start: ')
# df_CV_date.collect()[0]['test_start']


In [0]:
# # Assuming to use df_5yr_join_cv as a clean dataset

# Features_for_cv = ['CRS_DEP_DATETIME_UTC_END'] + ['ORI_station_id'] + Outcomes_for_flights + Features_for_flights + Features_for_weathers
# print(Features_for_cv)

# # [[train_start, train_end],[holdout_start, holdout_end]]
# cv_date_list=[[['2015-01-01', '2015-06-30'],['2015-07-01','2015-08-31']],
#              [['2015-06-01', '2015-11-30'],['2015-12-01', '2016-01-31']],
#              [['2015-11-01', '2016-04-30'],['2016-05-01', '2016-06-30']],
#              [['2016-04-01', '2016-09-30'],['2016-10-01', '2016-11-30']],
#              [['2016-09-01', '2017-02-28'],['2017-03-01', '2017-04-30']],
#              [['2017-02-01', '2017-07-31'],['2017-08-01', '2017-09-30']],
#              [['2017-07-01', '2017-12-31'],['2018-01-01', '2018-02-28']],
#              [['2017-12-01', '2018-05-31'],['2018-06-01', '2018-07-31']],
#              [['2018-05-01', '2018-10-31'],['2018-11-01', '2018-12-31']]]
# test_start_date = '2019-01-01'


# def CVSplit_full2(date_list,feature_list):
#   train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= date_list[0][0]) & (df_5yr_join_cv.DATE <= date_list[0][1]))
#   holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= date_list[1][0]) & (df_5yr_join_cv.DATE <= date_list[1][1]))
  
#   if 'DEP_DEL15' in feature_list:
#     train = train.select(feature_list)
#     holdout = holdout.select(feature_list)
#   else:
#     train = train.select(feature_list + ['DEP_DEL15'])
#     holdout = holdout.select(feature_list + ['DEP_DEL15'])
  
#   train_X = train.select(feature_list)
#   train_Y = train.select(['DEP_DEL15'])
#   holdout_X = holdout.select(feature_list)
#   holdout_Y = holdout.select(['DEP_DEL15'])
  
#   return train.cache(), holdout.cache()

# train0, holdout0 = CVSplit_full2(cv_date_list[0], Features_for_cv)
# train1, holdout1 = CVSplit_full2(cv_date_list[1], Features_for_cv)
# train2, holdout2 = CVSplit_full2(cv_date_list[2], Features_for_cv)
# train3, holdout3 = CVSplit_full2(cv_date_list[3], Features_for_cv)
# train4, holdout4 = CVSplit_full2(cv_date_list[4], Features_for_cv)
# train5, holdout5 = CVSplit_full2(cv_date_list[5], Features_for_cv)
# train6, holdout6 = CVSplit_full2(cv_date_list[6], Features_for_cv)
# train7, holdout7 = CVSplit_full2(cv_date_list[7], Features_for_cv)
# train8, holdout8 = CVSplit_full2(cv_date_list[8], Features_for_cv)

# trainAll = df_5yr_join_cv.filter(df_5yr_join_cv.DATE < test_start_date).select(Features_for_cv).cache()
# test = df_5yr_join_cv.filter(df_5yr_join_cv.DATE >= test_start_date).select(Features_for_cv).cache()

In [0]:
trainAll.columns

In [0]:
trainAll

# 3. Feature Selection with custom CV + new features as of April7

[Feature importanc result](https://docs.google.com/spreadsheets/d/15syDL-6Izk616mz96n6EUm3pqtBMT9rdblULbL2QIjA/edit?usp=sharing)

In [0]:
# bundle CV sets into lists and loop over zip of train, test. Keep running tracking array of recall, precision, f1 score. 
# if it works make it a wrapper function

# list of features NEW AS OF april7
features_list_full_april7 =  feature_list_full_0 + extra_features_added_april7
# label =  outcomes_for_flights

print(f"\nNumber of Features (Full) in feature_list_full_0: {len(features_list_full_april7)}")
print(features_list_full_april7)

# list of name of the dataset USE CUSTOM CV GROUPS
cv_group_list = [[train0_custom_april7, holdout0_custom_april7],
                 [train1_custom_april7, holdout1_custom_april7],
                 [train2_custom_april7, holdout2_custom_april7 ],
                 [train3_custom_april7, holdout3_custom_april7 ],
                 [train4_custom_april7, holdout4_custom_april7 ]]

# cv_group_list = [[train0, holdout0],[train1, holdout1],[train2,holdout2],
#                  [train3, holdout3],[train4, holdout4]]

cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

Number of Features (Full) in feature_list_full_0: 78
['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

In [0]:
len(train0_custom_april7.columns)

Out[46]: 80

In [0]:
cv_result

In [0]:
# Run Features importance
import timeit

start = timeit.default_timer()

# input of feature selection
features_for_RF = ['DEP_DEL15'] + features_list_full_april7

# define the container of output 
feature_importances_cv_loop = [['cv_group','loop_num'] + features_list_full_april7]

for i in range(3): # random number of loop
  for idx, dataset in enumerate(cv_group_list): # loop through cv split groups
    
    train = dataset[0].select(features_for_RF)
    holdout = dataset[1].select(features_for_RF)
  
    # Assembling #################################################################
    # Assemble features
    assembler = VectorAssembler().setInputCols(features_list_full_april7)\
                              .setOutputCol('features')

    assmb_train = assembler.transform(train)
    assmb_holdout = assembler.transform(holdout)
    
    # Random Forest Classifier ######################################################
    rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15')
    rfModel = rf.fit(assmb_train)
    predictions = rfModel.transform(assmb_holdout)
    
    # Feature importance in ######################################################
    feature_importance = rfModel.featureImportances
    feature_importances_cv_loop += [[idx,i] + list(feature_importance)]

    
stop = timeit.default_timer()
print('Time: ', stop - start)  

In [0]:
df_feature_importance = pd.DataFrame(feature_importances_cv_loop[1:], columns=feature_importances_cv_loop[0])

In [0]:
#df_feature_importance

In [0]:
df = spark.createDataFrame(df_feature_importance)
df.write.parquet(f"{blob_url}/df_RF_feature_importance_loop3_full_data_0407")

In [0]:
df = spark.read.parquet(f"{blob_url}/df_RF_feature_importance_loop3_full_data_0407")

In [0]:
display(df)

cv_group loop_num DISTANCE ORI_elevation DEST_elevation prior_dep_delayed previous_DEP_DELAY_NEW prior_arr_delayed previous_ARR_DELAY_NEW plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs daytime evening mid_atlantic south midwest southwest west pacific_islands atlantic_islands summer winter autumn weekend_or_holiday OC1_0_wind_gust_spd_rate_imp AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank avg_hourly_delay_24hr avg_OD_dep_del15_24hr avg_OD_delay_min_24hr avg_OD_num_flights_24hr depDelayPageRank_ordinal arrDelayPageRank_ordinal departed_for_current_aiport time_inb_flight_min avg_time_inb_flights_carrier_24hr avg_time_inb_flights_origin_24hr avg_time_inb_flights_dest_24hr avg_ori_DEP_DELAY_NEW_24hr airline_carrier_del airline_carrier_del_min avg_carrier_delay_over15_lastQ airline_carrier_del_ordinal airline_carrier_del_min_ordinal origin_avg_DEP_DEL15 origin_avg_DEP_DELAY_NEW avg_origin_delay_over15_lastQ origin_del_ordinal origin_del_min_ordinal OD_avg_DEP_DEL15 OD_avg_DEP_DELAY_NEW avg_OD_delay_over15_lastQ OD_del_ordinal OD_del_min_ordinal 2 0 5.583131396649714E-4 0.0 0.0 0.20290664482438092 0.2368395514307648 0.02021695804796565 0.026200426957528233 0.046893004711029876 0.01886356139232186 2.3024230255713177E-4 1.4611912905998387E-4 0.02777562040851153 0.01721088300940677 0.03582453800932406 0.0 0.0 6.338192447391191E-5 0.0 0.0 6.209814827392794E-4 0.0 0.0 0.0 1.6978113074346676E-4 0.0 0.0 3.149017340644483E-5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 7.037195084966351E-5 0.0 0.0 0.0 8.647173822731398E-4 0.0 0.0 0.0018394117259468614 0.0 5.342586431848897E-4 0.002963796394210183 1.5176182875614616E-4 0.0 0.0 0.0 4.7010202398896205E-5 0.0 0.08352625570392914 0.035273401595391475 0.0032663464772004366 0.0 1.8832681055036885E-4 3.8387966922299506E-4 0.005267068914001983 0.18778749803932362 1.678349268619193E-4 2.492205858348125E-5 0.0 0.019035727441841413 5.956399441720553E-4 0.0011882726538803593 0.0 6.820748313527052E-4 3.9021162148768283E-4 0.0 5.9823463140019655E-6 0.0 0.0 0.0 0.011602750376401502 1.570417290399041E-4 0.0020357008392971844 0.005741405975898197 0.0016568318437508104 2 1 5.583131396649714E-4 0.0 0.0 0.20290664482438092 0.2368395514307648 0.02021695804796565 0.026200426957528233 0.046893004711029876 0.01886356139232186 2.3024230255713177E-4 1.4611912905998387E-4 0.02777562040851153 0.01721088300940677 0.03582453800932406 0.0 0.0 6.338192447391191E-5 0.0 0.0 6.209814827392794E-4 0.0 0.0 0.0 1.6978113074346676E-4 0.0 0.0 3.149017340644483E-5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 7.037195084966351E-5 0.0 0.0 0.0 8.647173822731398E-4 0.0 0.0 0.0018394117259468614 0.0 5.342586431848897E-4 0.002963796394210183 1.5176182875614616E-4 0.0 0.0 0.0 4.7010202398896205E-5 0.0 0.08352625570392914 0.035273401595391475 0.0032663464772004366 0.0 1.8832681055036885E-4 3.8387966922299506E-4 0.005267068914001983 0.18778749803932362 1.678349268619193E-4 2.492205858348125E-5 0.0 0.019035727441841413 5.956399441720553E-4 0.0011882726538803593 0.0 6.820748313527052E-4 3.9021162148768283E-4 0.0 5.9823463140019655E-6 0.0 0.0 0.0 0.011602750376401502 1.570417290399041E-4 0.0020357008392971844 0.005741405975898197 0.0016568318437508104 2 2 5.583131396649714E-4 0.0 0.0 0.20290664482438092 0.2368395514307648 0.02021695804796565 0.026200426957528233 0.046893004711029876 0.01886356139232186 2.3024230255713177E-4 1.4611912905998387E-4 0.02777562040851153 0.01721088300940677 0.035824538009

In [0]:
df.columns

## Selected Features

In [0]:
# 'daytime' is removed
selected_features_tier1 = ['DEST_elevation','prior_dep_delayed','previous_DEP_DELAY_NEW','prior_arr_delayed',
                           'previous_ARR_DELAY_NEW','plane_is_here','avg_carrier_delay_24hrs',
                           'avg_ori_airport_delay_24hrs','evening','avg_hourly_delay_24hr','avg_OD_dep_del15_24hr','time_inb_flight_min',
                           'avg_ori_DEP_DELAY_NEW_24hr','OD_avg_DEP_DEL15']

selected_features_tier1_2 = ['DISTANCE','ORI_elevation','DEST_elevation','prior_dep_delayed','previous_DEP_DELAY_NEW','prior_arr_delayed',
                             'previous_ARR_DELAY_NEW','plane_is_here','avg_carrier_delay_24hrs','flights_sch_Today_ORIGIN','flights_sch_Today_DEST',
                             'avg_ori_airport_delay_24hrs','evening','pacific_islands','summer','OC1_0_wind_gust_spd_rate_imp','AA1_1_liquid_precip',
                             'aw1_mw1_0_rain_drizzle','aw1_mw1_0_snow','aw1_mw1_0_thunderstorm','WND_3_wind_speed_imp','CIG_0_sky_ceiling_height_imp',
                             'VIS_0_visibility_dist_imp','TMP_0_air_temperature_imp','DEW_0_dew_pt_temp_imp','MA1_0_altimeter_set_rate_imp','depDelayPageRank',
                             'arrDelayPageRank','avg_hourly_delay_24hr','avg_OD_dep_del15_24hr','avg_OD_delay_min_24hr','depDelayPageRank_ordinal',
                             'arrDelayPageRank_ordinal','departed_for_current_aiport','time_inb_flight_min','avg_time_inb_flights_dest_24hr',
                             'avg_ori_DEP_DELAY_NEW_24hr','airline_carrier_del','airline_carrier_del_min','airline_carrier_del_ordinal',
                             'airline_carrier_del_min_ordinal','origin_avg_DEP_DEL15','origin_avg_DEP_DELAY_NEW','OD_avg_DEP_DEL15',
                             'avg_OD_delay_over15_lastQ','OD_del_ordinal','OD_del_min_ordinal']

In [0]:
print(len(selected_features_tier1))
print(len(selected_features_tier1_2))

# 4. Quick hyperparameter tuning with 3yr + 1yr full data

## Create a split for 3years + 1year

In [0]:
# dataset : df_5yr_join_cv_april7
features_list =  feature_list_full_0 + extra_features_added_april7
features_for_cv = features_for_cv_april7

In [0]:

# name latest record as "latest_record"
df_CV_date = df_5yr_join_cv_april7.select(max("DATE")).withColumnRenamed("max(DATE)","latest_record")
# name the start date of test data as test_start

df_CV_date = df_CV_date.withColumn("test_start_", add_months("latest_record",-12))
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("test_start", date_add("test_start_",+1))


# start date of cv group1: train0
df_CV_date = df_CV_date.withColumn("train0_", add_months("latest_record",-60)).cache()
# the line is unnecessary added because 20200101 is cut
df_CV_date = df_CV_date.withColumn("train0", date_add("train0_",+1))

# start date of cv group1: holdout0
df_CV_date = df_CV_date.withColumn("holdout0", add_months("train0",+36))

display(df_CV_date)

# use pandas because operation is much lighter
pdf_CV_date = df_CV_date.cache().toPandas()
print(pdf_CV_date)

# list of name of the dataset
cv_group_list = [['train0','holdout0']]

def CVSplit_full1(df, cv_group, feature_list):
  
  global pdf_CV_date#df_CV_date
  
  # assign start date
  train_start_date = pdf_CV_date[cv_group[0]][0]
  holdout_start_date = pdf_CV_date[cv_group[1]][0]
  print(f'{cv_group[0]}_start: {train_start_date}, {cv_group[1]}_start: {holdout_start_date}')

  # calculate end date of train/holdout data
  pdf_CV_date[cv_group[0]+'_end'] = train_start_date + relativedelta(months=+5)
  pdf_CV_date[cv_group[1]+'_end'] = holdout_start_date + relativedelta(months=+2)
  
  # calculate end date of train/holdout data
  train_end_date = train_start_date + relativedelta(months=+36) - timedelta(days=1)
  holdout_end_date = holdout_start_date + relativedelta(months=+12) - timedelta(days=1)
  print(f'{cv_group[0]}_end:   {train_end_date}, {  cv_group[1]}_end:   {holdout_end_date}')
    
  # train = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= train_start_date) & (df_5yr_join_cv.DATE <= train_end_date))
  # holdout = df_5yr_join_cv.filter((df_5yr_join_cv.DATE >= holdout_start_date) & (df_5yr_join_cv.DATE <= holdout_end_date))
  train = df.filter((df.DATE >= train_start_date) & (df.DATE <= train_end_date))
  holdout = df.filter((df.DATE >= holdout_start_date) & (df.DATE <= holdout_end_date))
  
  train = train.select(features_for_cv_april7).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  holdout = holdout.select(features_for_cv_april7).cache()# + ['DATE']) # have date column to check if the date is splitted correctly
  
  print(f"flights in {cv_group[0]}: {train.count()}, flights in {cv_group[1]}: {holdout.count()}")
  
  return train, holdout

train_3yrs, holdout_1yr= CVSplit_full1(df_5yr_join_cv_april7, cv_group_list[0], features_for_cv_april7)

## Tune models with hyperopt

In [0]:
from sklearn.datasets import fetch_openml
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.utils import check_random_state

from hyperopt import fmin, hp, tpe
from hyperopt import SparkTrials, STATUS_OK, Trials
from hyperopt.pyll import scope
import hyperopt

## 4-1. Define list/df to store the records of tuning

In [0]:
selected_features_tier1_2

In [0]:
cv_group_list = [[train_3yrs, holdout_1yr]]

# tier 1  (criteria of 2 > 0.005)
# tier 1 + 2 (criteria of 2 > 0.0001)
feature_list = selected_features_tier1_2

# hyper parameter list that we want to store the records
# align the parameters that you are setting in the "search space"
parameter_dict = {'maxDepth':[],'maxBins':[],'numTrees':[],'minInstancesPerNode':[]}

# store cv result for each cv group
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

# store best parameter in each cv group
best_hyperparameters_df = pd.DataFrame()

## Option. Create a flow for logging
- Not necessary but nice to have

In [0]:
import mlflow
# As explained in Cmd 2 of this notebook, MLflow autologging for `pyspark.ml` requires MLflow version 1.17.0 or above.
# This try-except logic allows the notebook to run with older versions of MLflow.
try:
  import mlflow.pyspark.ml
  mlflow.pyspark.ml.autolog()
except:
  print(f"Your version of MLflow ({mlflow.__version__}) does not support pyspark.ml for autologging. To use autologging, upgrade your MLflow client version or use Databricks Runtime for ML 8.3 or above.")

## 4-2. Define function to train a model
- Define a function that trains the model
- Wrapping the training code in a function is important for passing the function to Hyperopt for tuning later.

In [0]:
def train_RF(params, train, holdout):
  """
  main training function which we pass to Hyperopt.
  It takes in hyperparameter settings, fits a model based on those settings,
  evaluates the model, and returns the loss.

  :param params: map specifying the hyperparameter settings to test
  :return: loss for the fitted model
  """
  
  global cv_result, CV_group_num
  
  # change "DEP_DEL15" to "label"
  train = train.withColumnRenamed("DEP_DEL15","label")
  holdout = holdout.withColumnRenamed("DEP_DEL15","label")
  
  with mlflow.start_run(nested=True):
    # modeling
    rf = RandomForestClassifier()
    
    # params contains the dictionary of randomly picked hyper parameters
    # we need to assign hyper parameters in the params to model
    
    # print parameters that we are assigning to the model
    print(f'CV_group: {CV_group_num}, Parameters: {params}') 
    for k in params.keys():
        # getParam: funtion of RF classifier in pySpark
        p = rf.getParam(k) 
        # model.set(): Assign parameter to the model(funtion of RF classifier in pySpark)
        rf.set(p, params[k])
        
        # add values of each parameter to dictionary
        parameter_dict[k].append(params[k])
    
    # fit the model
    rfModel = rf.fit(train)
    predictions = rfModel.transform(holdout)

    # gain result of the prediction
    results = predictions.select(['prediction', 'label'])
    metrics = MulticlassMetrics(results.rdd)
    f1 = metrics.fMeasure(1.0,1.0)

    #  Update the result and store the record to list/df
    #  cv_result_run = ['CV_group','Accuracy','Recall','Precision','f1_score']
    cv_result_run = [[CV_group_num, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]
    cv_result += cv_result_run

    print(f'CV_group: {CV_group_num}, Accuracy: {metrics.accuracy}, Recall: {metrics.recall(label=1)},Precision: {metrics.precision(1)}, F1_score: {metrics.fMeasure(1.0,1.0)}')
  return f1, cv_result

## 4-3. Define search space

In [0]:
# look at Cmd just before the "End of hyperopt" to see the options that we could apply to search space
# WARNING: If we choose "choice", parameters are returned as index. If maxBins = 16 is the best, 0 is returned as value
search_space = {
    'maxDepth': hp.quniform('maxDepth', 3,8,q=1),#,#range(3,10)),
    'maxBins': hp.choice('maxBins',[16,32,64,128]),
    'numTrees': hp.choice('numTrees', [20, 60, 100, 150]),
    'minInstancesPerNode': hp.choice('minInstancesPerNode',[1,5,10,50,100])
    }

#### Option: Selecting only the features that we are using could be safer to avoid error

## 4-4. Tune the model with hyperopt

### 4-4-1. Tune a single cv group
- If you want to run all the cv groups, go to the next section

In [0]:
cv_group_list = [[train_3yrs, holdout_1yr]]
CV_group_num = 1
CV_group = [train_3yrs, holdout_1yr]

best_hyperparameters_df_ = pd.DataFrame()

# for CV_group_num, CV_group in enumerate(cv_group_list):

# Assemble features
assembler_tmp = VectorAssembler().setInputCols(feature_list)\
                          .setOutputCol('features')

assmb_train_tmp = assembler_tmp.transform(CV_group[0])
assmb_holdout_tmp = assembler_tmp.transform(CV_group[1])


# defining hyperopt_f to keep the best f1 score
# 'loss' is the default description in hyperopt. 
  # It is to design to minimize, therefore we need to use -f1 to maximize the value
count = 0
best = 0
def hyperopt_f(params):
  global best, count #, #cv_result, CV_group_num
  count += 1
  f1, cv_result = train_RF(params.copy(),assmb_train_tmp, assmb_holdout_tmp)
  if f1 > best:
    print(f'new best: {f1}')
    best = f1
  if count % 50 == 0:
      print(f'iters: {count}, f1: {f1} using {params}')
  return {'loss': -(f1), 'status': STATUS_OK}

# trials stores the record but we did not use here
trials = Trials()
# fmin is the default function of hyperopt. see official doc for detalils
best_hyperparameters = fmin(fn=hyperopt_f,
                            space=search_space,
                            algo=tpe.suggest, # We have random.tpe.suggest as an option, but tpe.suggest if commonly used in hyperopt
                            max_evals=20, # how many combinations of parameters we would like to try
                            verbose=1)
print(f'CV_group_num: {CV_group_num}, f1: {best}, best_hyperparameters: {best_hyperparameters}')

# update dataframe that stores the result
best_hyperparameters_df = pd.concat([best_hyperparameters_df,pd.DataFrame([best_hyperparameters])], axis=0)
pd.DataFrame([best_hyperparameters]) 

best_hyperparameters_df

In [0]:
best_hyperparameters_df

In [0]:
# search_space = {
#     'maxDepth': hp.quniform('maxDepth', 3,8,q=1),#,#range(3,10)),
#     'maxBins': hp.choice('maxBins',[16,32,64,128]),
#     'numTrees': hp.choice('numTrees', [20, 60, 100, 150]),
#     'minInstancesPerNode': hp.choice('minInstancesPerNode',[1,5,10,50,100])
#     }

# {'maxBins': 32, 'maxDepth': 4.0, 'minInstancesPerNode': 10, 'numTrees': 100}
# {'maxBins': 128, 'maxDepth': 4.0, 'minInstancesPerNode': 50, 'numTrees': 150}
# {'maxBins': 64, 'maxDepth': 7.0, 'minInstancesPerNode': 100, 'numTrees': 60}
# {'maxBins': 64, 'maxDepth': 8.0, 'minInstancesPerNode': 10, 'numTrees': 100}

# best parameters
# {'maxBins': 2, 'maxDepth': 8.0, 'minInstancesPerNode': 2, 'numTrees': 2}

# maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100


# 5. Simple Run with Selected Features

[spread sheet](https://docs.google.com/spreadsheets/d/15syDL-6Izk616mz96n6EUm3pqtBMT9rdblULbL2QIjA/edit?usp=sharing)

In [0]:
#April7 version 

# selected features

# tier 1 (criteria of 1 > 0.005)
print(f'selected_features_tier1: {len(selected_features_tier1)}')
print(f'{selected_features_tier1}')

# tier 1 + 2 (criteria of 2 > 0.0001)
print(f'selected_features_tier1 & 2: {len(selected_features_tier1_2)}')
print(f'{selected_features_tier1_2}')

# original features
print(f'feature_list_full_0: {len(feature_list_full_0)}')
print(f'{feature_list_full_0}')

cv_group_list = [[train0_custom_april7, holdout0_custom_april7],
                 [train1_custom_april7, holdout1_custom_april7],
                 [train2_custom_april7, holdout2_custom_april7 ],
                 [train3_custom_april7, holdout3_custom_april7 ],
                 [train4_custom_april7, holdout4_custom_april7 ]]

selected_features_tier1: 14
['DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'avg_ori_airport_delay_24hrs', 'evening', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'time_inb_flight_min', 'avg_ori_DEP_DELAY_NEW_24hr', 'OD_avg_DEP_DEL15']
selected_features_tier1 & 2: 47
['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'evening', 'pacific_islands', 'summer', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_thunderstorm', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'depDelayPageRank', 'arrDelayPageRank', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'OD_avg_DEP_DEL15', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']
feature_list_full_0: 51
['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'atlantic_islands', 'summer', 'winter', 'autumn', 'weekend_or_holiday', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'depDelayPageRank', 'arrDelayPageRank']

In [0]:
#RandomForestClassifier(*, featuresCol='features', labelCol='label', predictionCol='prediction', probabilityCol='probability', rawPredictionCol='rawPrediction', 
                        #maxDepth=5, maxBins=32, minInstancesPerNode=1, minInfoGain=0.0, maxMemoryInMB=256, cacheNodeIds=False, checkpointInterval=10,
                        #impurity='gini', numTrees=20, featureSubsetStrategy='auto', seed=None, subsamplingRate=1.0, leafCol='', minWeightFractionPerNode=0.0, 
                        #weightCol=None, bootstrap=True)

### Function for RF

In [0]:
def runCV_RandomForest(cv_dataset, feature_list, verbose=0, rebalance_input_tup=(True, 1.6),
                       maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345):
  
  """
  Wrapper function to run Random Forest cross validation.
  Inputs:
  - cv_dataset: list of lists of test & holdout.
  - feature_list: list of str names of features
  - verbose: [0, 1, 2] as verbosity level. 0 means nothing printed. 1 means summary stats printed. 2 means everything printed.
  - rebalance_input_tup: To be updated
  - rest of the parameters: hyperparameters for RF
  Outputs:
  - df_cv_result_0: pandas dataframe of each CV result
  - mean_pd_df: pandas dataframe of the mean of the CV results. This is what we look at to assess performance of CV.
  """
  if rebalance_input_tup[0]:
    rebalancing, desired_neg_to_pos_ratio = rebalance_input_tup
    rebalancing = True
  else:
    rebalancing = False
  
  def rebalanceDF(trainingDF, desired_neg_to_pos_ratio):
    original_dep_del15_count_df = trainingDF.groupby('DEP_DEL15').count()
    positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
    negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]

    # undersampling the negative cases
    negativeDF = trainingDF.filter(trainingDF['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
    positiveDF = trainingDF.filter(trainingDF['DEP_DEL15']==1)
    new_trainDF = positiveDF.union(negativeDF).cache()
    return new_trainDF
  
  print(f"Random Forest, maxDepth={maxDepth}, maxBins={maxBins},minInstancesPerNode={minInstancesPerNode}, numTrees={numTrees}")
#         minInfoGain={minInfoGain}, maxMemoryInMB={maxMemoryInMB},\
#         cacheNodeIds={cacheNodeIds}, checkpointInterval={checkpointInterval}, impurity={impurity}, \
#         featureSubsetStrategy={featureSubsetStrategy}, seed={seed}, subsamplingRate={subsamplingRate}, leafCol={leafCol},\
#         minWeightFractionPerNode={minWeightFractionPerNode}, weightCol={weightCol}, bootstrap={bootstrap}")
        
  
  # instantiate pandas bookkeeping of metrics
  cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]
  
  num_cv = len(cv_dataset)
  maxDepth_lst = [maxDepth]*num_cv
  maxBins_lst = [maxBins]*num_cv
  minInstancesPerNode_lst = [minInstancesPerNode]*num_cv
#   minInfoGain_lst = [minInfoGain]*num_cv
#   maxMemoryInMB_lst = [maxMemoryInMB]*num_cv
#   cacheNodeIds_lst = [cacheNodeIds]*num_cv
#   checkpointInterval_lst = [checkpointInterval]*num_cv
#   impurity_lst = [impurity]*num_cv
  numTrees_lst = [numTrees]*num_cv
#   featureSubsetStrategy_lst = [featureSubsetStrategy]*num_cv
#   seed_lst = [seed]*num_cv
#   subsamplingRate_lst = [subsamplingRate]*num_cv
#   leafCol_lst = [leafCol]*num_cv
#   minWeightFractionPerNode_lst = [minWeightFractionPerNode]*num_cv
#   weightCol_lst = [weightCol]*num_cv
#   bootstrap_lst = [bootstrap]*num_cv
  times = []
  
  for i in range(len(cv_dataset)):
    if verbose > 1:
      print(f"Training CV {i}...")
    if not rebalancing:
      start = time.time()
      cv_result += RandomForestCV(train=cv_dataset[i][0], holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed,CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
    else:
      start = time.time()
      # rebalance cv_dataset[i][0]
      new_trainDF = rebalanceDF(cv_dataset[i][0], desired_neg_to_pos_ratio)
      
      cv_result += RandomForestCV(train=new_trainDF, holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode,numTrees=numTrees,seed=seed, 
                                  CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
  
  # append columns for tuned hyperparameters
  df_cv_result_0 = pd.DataFrame(cv_result[1:],columns=cv_result[0])
  df_cv_result_0["maxDepth"] = maxDepth_lst
  df_cv_result_0["maxBins"] = maxBins_lst
  df_cv_result_0["minInstancesPerNode"] = minInstancesPerNode_lst
  df_cv_result_0["numTrees"] = numTrees_lst
  df_cv_result_0["time"] = times
  
  if verbose > 1:
    display(df_cv_result_0)
  
  # make the means_df
  mean_pd_df = df_cv_result_0.groupby(['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees'])[['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'Accuracy','Recall','Precision','f1_score', 'time']].mean()
  
  if verbose > 0:
    display(mean_pd_df)
  return df_cv_result_0, mean_pd_df

In [0]:
def runCV_RandomForest_simple(cv_dataset, feature_list, verbose=0, rebalance_input_tup=(True, 1.6),
                      maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345):
  """
  Wrapper function to run Random Forest cross validation.
  Inputs:
  - cv_dataset: list of lists of test & holdout.
  - feature_list: list of str names of features
  - verbose: [0, 1, 2] as verbosity level. 0 means nothing printed. 1 means summary stats printed. 2 means everything printed.
  - rebalance_input_tup: To be updated
  - rest of the parameters: hyperparameters for RF
  Outputs:
  - df_cv_result_0: pandas dataframe of each CV result
  - mean_pd_df: pandas dataframe of the mean of the CV results. This is what we look at to assess performance of CV.
  """
  if rebalance_input_tup[0]:
    rebalancing, desired_neg_to_pos_ratio = rebalance_input_tup
    rebalancing = True
    rebalancing_ratio_lst = [desired_neg_to_pos_ratio]*len(cv_dataset)
  else:
    rebalancing = False
  
  def rebalanceDF(trainingDF, desired_neg_to_pos_ratio):
    original_dep_del15_count_df = trainingDF.groupby('DEP_DEL15').count()
    positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
    negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]

    # undersampling the negative cases
    negativeDF = trainingDF.filter(trainingDF['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
    positiveDF = trainingDF.filter(trainingDF['DEP_DEL15']==1)
    new_trainDF = positiveDF.union(negativeDF).cache()
    return new_trainDF
  
  print(f"Random Forest, maxDepth={maxDepth}, maxBins={maxBins}, minInstancesPerNode={minInstancesPerNode}, numTrees={numTrees}, seed={seed}")
  
  # instantiate pandas bookkeeping of metrics
  cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]
  
  num_cv = len(cv_dataset)
  maxDepth_lst = [maxDepth]*num_cv
  maxBins_lst = [maxBins]*num_cv
  minInstancesPerNode_lst = [minInstancesPerNode]*num_cv
#   minInfoGain_lst = [minInfoGain]*num_cv
#   maxMemoryInMB_lst = [maxMemoryInMB]*num_cv
#   cacheNodeIds_lst = [cacheNodeIds]*num_cv
#   checkpointInterval_lst = [checkpointInterval]*num_cv
#   impurity_lst = [impurity]*num_cv
  numTrees_lst = [numTrees]*num_cv
#   seed_lst = [seed]*num_cv
  times = []
  
  for i in range(len(cv_dataset)):
    if verbose > 1:
      print(f"Training CV {i}...")
    if not rebalancing:
      start = time.time()
      cv_result += RandomForestCV_simple(train=cv_dataset[i][0], holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed, CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
    else:
      start = time.time()
      # rebalance cv_dataset[i][0]
      new_trainDF = rebalanceDF(cv_dataset[i][0], desired_neg_to_pos_ratio)
      
      cv_result += RandomForestCV_simple(train=new_trainDF, holdout=cv_dataset[i][1], feature_list=feature_list, 
                                  maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed,
                                  CV_group=i, verbose=verbose)
      end = time.time()
      time_delta = end - start
      times.append(time_delta)
  
  # append columns for tuned hyperparameters
  df_cv_result_0 = pd.DataFrame(cv_result[1:],columns=cv_result[0])
  df_cv_result_0["maxDepth"] = maxDepth_lst
  df_cv_result_0["maxBins"] = maxBins_lst
  df_cv_result_0["minInstancesPerNode"] = minInstancesPerNode_lst
  df_cv_result_0["numTrees"] = numTrees_lst
  df_cv_result_0["time"] = times
  
  if rebalancing:
    df_cv_result_0["desired_neg_to_pos_ratio"] = rebalancing_ratio_lst
  
  if verbose > 1:
    display(df_cv_result_0)
  
  # make the means_df
  if rebalancing:
    mean_pd_df = df_cv_result_0.groupby(['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'desired_neg_to_pos_ratio'])[['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'desired_neg_to_pos_ratio', 'Accuracy','Recall','Precision','f1_score', 'time']].mean()
  else:
    mean_pd_df = df_cv_result_0.groupby(['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees'])[['maxDepth', 'maxBins', 'minInstancesPerNode', 'numTrees', 'Accuracy','Recall','Precision','f1_score', 'time']].mean()
  
  if verbose > 0:
    display(mean_pd_df)
  return df_cv_result_0, mean_pd_df

## Custom RF function that stores the prediction table

In [0]:
def RFwithPredictionDf(CV_group, train, holdout, feature_list, verbose=0, rebalance_input_tup=(True, 1.6),
                     maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345):
  """
  Wrapper function to run Random Forest that stores prediction table.
  Inputs:
  - cv_dataset: list of lists of test & holdout.
  Outputs:
  - df_cv_result_0: pandas dataframe of each CV result
  - 
  """
  cv_dataset=[1,2,3,4,5]
  
  if rebalance_input_tup[0]:
    rebalancing, desired_neg_to_pos_ratio = rebalance_input_tup
    rebalancing = True
    rebalancing_ratio_lst = [desired_neg_to_pos_ratio]*len(cv_dataset)
  else:
    rebalancing = False
  
  def rebalanceDF(trainingDF, desired_neg_to_pos_ratio):
    original_dep_del15_count_df = trainingDF.groupby('DEP_DEL15').count()
    positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
    negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]

    # undersampling the negative cases
    negativeDF = trainingDF.filter(trainingDF['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
    positiveDF = trainingDF.filter(trainingDF['DEP_DEL15']==1)
    new_trainDF = positiveDF.union(negativeDF).cache()
    return new_trainDF
  
  print(f"Random Forest, maxDepth={maxDepth}, maxBins={maxBins}, minInstancesPerNode={minInstancesPerNode}, numTrees={numTrees}, seed={seed}")
  
  # instantiate pandas bookkeeping of metrics
  cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]
  
  
  if verbose > 1:
    print(f"Training CV {i}...")
  if not rebalancing:
    start = time.time()
    
    # Assemble features
    assembler = VectorAssembler().setInputCols(feature_list).setOutputCol('features')
    assmb_train = assembler.transform(train)
    assmb_holdout = assembler.transform(holdout)

    # modeling
    rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                                maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed)
    rfModel = rf.fit(assmb_train)
    predictions = rfModel.transform(assmb_holdout)

    feature_for_analysis = ['DATE','DEP_DEL15','probability','prediction','features', 'rawPrediction']
    analysis_df = predictions.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')
    metrics = MulticlassMetrics(results.rdd)

    # ['CV_group','Accuracy','Recall','Precision','f1_score']
#     cv_result_run = [[CV_group, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]

    end = time.time()
    time_delta = end - start
    
  else:
    start = time.time()
    # rebalance cv_dataset[i][0]
    new_trainDF = rebalanceDF(train, desired_neg_to_pos_ratio)
    
    # Assemble features
    assembler = VectorAssembler().setInputCols(feature_list).setOutputCol('features')
    assmb_train = assembler.transform(new_trainDF)
    assmb_holdout = assembler.transform(holdout)

    # modeling
    rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                                maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed)
    rfModel = rf.fit(assmb_train)
    predictions = rfModel.transform(assmb_holdout)

    feature_for_analysis = ['DATE','DEP_DEL15','probability','prediction','features', 'rawPrediction']
    analysis_df = predictions.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')
    metrics = MulticlassMetrics(analysis_df.rdd)

    # ['CV_group','Accuracy','Recall','Precision','f1_score']
#     cv_result_run = [[CV_group, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]
#     print(f'CV_group:{CV_group}, Accuracy:{metrics.accuracy}, Recall: {metrics.recall(label=1)}, Precision: {metrics.precision(1)}, f1_score:{metrics.fMeasure(1.0,1.0)}')
    
    end = time.time()
    time_delta = end - start

  return analysis_df

## Run Custom CV model + New Features(Tier1+Tier2)

In [0]:
analysis_df_0 = RFwithPredictionDf(1, train0_custom_april7, holdout0_custom_april7, selected_features_tier1_2, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

Random Forest, maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345

In [0]:
display(analysis_df_0)

DATE label probability prediction features rawPrediction 2016-07-02T18:00:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6438436287878243, 0.35615637121217575)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.52, 27.0, 202.0, 0.15, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 31.0, 11524.85510428101, 16000.0, 211.0, 144.0, 10135.871569703622, 0.003500544675913835, 0.0027747531201398517, 0.241, 0.15, 9.029411764705882, 66.0, 82.0, 0.0, 64.0, 330.3, 9.029411764705882, 0.2174832779656472, 14.362938906848212, 3.0, 2.0, 0.15740380878352117, 9.674698795180722, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(64.38436287878241, 35.61563712121757)) 2016-07-03T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7737283299801707, 0.22627167001982929)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 1.0, 60.0, 1.0, 56.0, 1.0, 0.18, 18.0, 291.0, 0.05, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 110.0, 30.0, 10213.0, 0.0026349144472628, 0.0025650351982225914, 0.084, 0.05, 4.35, 81.0, 87.0, 1.0, 610.0, 481.47, 4.35, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(77.37283299801706, 22.627167001982926)) 2016-07-05T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7451930279798183, 0.25480697202018165)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.1, 18.0, 391.0, 0.29, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 110.0, 30.0, 10186.0, 0.0026349144472628, 0.0025650351982225914, 0.078, 0.29, 27.142857142857142, 81.0, 87.0, 1.0, 681.0, 697.89, 27.142857142857142, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(74.51930279798184, 25.480697202018167)) 2016-07-06T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8008263388860298, 0.19917366111397017)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.17, 18.0, 392.0, 0.11, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 15.0, 3353.0, 16093.0, 80.0, 30.0, 10173.0, 0.0026349144472628, 0.0025650351982225914, 0.11, 0.0, 0.0, 81.0, 87.0, 1.0, 681.0, 438.94, 4.833333333333333, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(80.08263388860301, 19.917366111397026)) 2016-07-07T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7619175131735116, 0.23808248682648833)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.22, 17.0, 391.0, 0.22, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 26.0, 22000.0, 16093.0, 20.0, -10.0, 10196.0, 0.0026349144472628, 0.0025650351982225914, 0.134, 0.0, 0.0, 81.0, 87.0, 1.0, 669.0, 820.54, 6.444444444444445, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(76.19175131735118, 23.808248682648838)) 2016-07-08T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8022482292200129, 0.19775177077998712)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.24, 17.0, 392.0, 0.06, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 40.0, 10.0, 10217.0, 0.0026349144472628, 0.0025650351982225914, 0.094, 0.0, 0.0, 81.0, 87.0, 1.0, 674.0, 406.17, 4.352941176470588, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333

In [0]:
analysis_df = analysis_df_0
search_space = [0.2]

# Based on the dataframe with prob_1 and prob_0, convert the spark df to pandas df with TP/TN/FP/FN, calculate f1 score and returns the df of the result
def f1_Eval(search_space, analysis_df):

  f1_by_threshold = [['index','threshold','f1_score']]
  best_f1_score = 0
  best_f1_index = 0
  best_threshold = 0

  analysis_df_th = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))

  for idx, threshold in enumerate(search_space):
    #global f1_by_threshold, analysis_df_th, best_f1_score
    print(f'threshold:{threshold}')
    
    def pred_by_threshold(x): #x: prob_1
      global threshold
      print(f'threshold: {threshold}, x: {x}')
      try:
        if x >= threshold:
            print(int(1))
            return int(1)
        elif x < threshold:
            print(int(1))
            return int(0)
      except ValueError:
            return None
    pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())

    # add column of prediction 
    analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
    # add evaluation column     
    analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label'))
    display(analysis_df_th)

    # gain a result
    result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
    pdf_result = result.toPandas()
    print(pdf_result)

    TPTNFPFN_list = [i for i in pdf_result["eval_"+str(idx)]]
    if "TP" in TPTNFPFN_list:
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    elif "TP" not in TPTNFPFN_list:
      TP = 0
    if "TN" in TPTNFPFN_list:
      TN = list(pdf_result[pdf_result["eval_"+str(idx)]=='TN']['count'])[0]
    elif "TN" not in TPTNFPFN_list:
      TN = 0
    if "FP" in TPTNFPFN_list:
      FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    elif "FP" not in TPTNFPFN_list:
      FP = 0
    if "FN" in TPTNFPFN_list:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
    elif "FN" not in TPTNFPFN_list:
      FN = 0

    # count TP/FP/FN and return zero if denominator/numerator of f1 is zero
    if 2*TP+FN+FP == 0:
      f1_score = 0
    elif 2*TP+FN+FP != 0:
      f1_score = 2*TP/(2*TP+FN+FP)
    print(f1_score)

    f1_by_threshold += [[idx,threshold,f1_score]]
    print(f1_by_threshold)

    if f1_score > best_f1_score:
      best_f1_score = f1_score
      best_f1_index = idx
      best_threshold = threshold
    print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best_f1_index: {best_f1_index}, best_threshold: {best_threshold }, best f1 score: {best_f1_score}')

  return f1_by_threshold, analysis_df_th, best_f1_score, best_f1_index, best_threshold

In [0]:
f1_by_threshold, analysis_df_th, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_0)

In [0]:
analysis_df_th = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))

  for idx, threshold in enumerate(search_space):
    #global f1_by_threshold, analysis_df_th, best_f1_score
    print(f'threshold:{threshold}')
    
    def pred_by_threshold(x): #x: prob_1
      global threshold
      print(f'threshold: {threshold}, x: {x}')
      try:
        if x >= threshold:
            print(int(1))
            return int(1)
        elif x < threshold:
            print(int(1))
            return int(0)
      except ValueError:
            return None
    pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())

    # add column of prediction 
    analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
    # add evaluation column     
    analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label'))
    display(analysis_df_th)


In [0]:
print(f'f1_by_threshold: {f1_by_threshold}')
print(f'analysis_df_th: {analysis_df_th}')
print(f'best_f1_score: {best_f1_score}')
print(f'best_f1_index: {best_f1_index}')
print(f'best_threshold: {best_threshold}')

In [0]:
selected_features_match_XGboost = ['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'new_england', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'spring', 'winter', 'autumn', 'weekend_or_holiday', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'previous_ARR_DELAY_NEW', 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs', 'depDelayPageRank', 'arrDelayPageRank', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

In [0]:
analysis_df_1 = RFwithPredictionDf(2, train1_custom_april7, holdout1_custom_april7, selected_features_tier1_2, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

Random Forest, maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345

In [0]:

display(analysis_df_1)

DATE label probability prediction features rawPrediction 2017-06-13T08:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7524733062069368, 0.24752669379306333)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(554.0, 629.0, 645.0, 1.0, 64.0, 1.0, 43.0, 1.0, 0.2, 13.0, 375.0, 0.33, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 26.0, 22000.0, 16093.0, 222.0, 211.0, 10190.0, 0.001928335260711345, 9.591543174998489E-4, 0.061, 0.33, 21.333333333333332, 115.0, 207.0, 1.0, 479.0, 272.13, 21.333333333333332, 0.18356550756111126, 15.976601604915384, 8.0, 4.0, 0.09988109393579073, 8.745541022592151, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(75.24733062069367, 24.752669379306333)) 2017-05-04T01:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6778890986970101, 0.3221109013029899)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 5.0, 0.0, 0.0, 0.0, 0.25, 45.0, 220.0, 0.13, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 46.0, 22000.0, 16093.0, 228.0, 94.0, 10125.0, 0.005741130701079948, 0.0031661684465465866, 0.199, 0.13, 5.5777777777777775, 44.0, 74.0, 1.0, 56.0, 331.21, 5.5777777777777775, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.22755417956656346, 15.849587203302374, 1.0, 1.0, 1.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(67.78890986970102, 32.211090130299)) 2017-05-05T01:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6546128985748196, 0.3453871014251805)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.24, 45.0, 231.0, 0.09, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 46.0, 22000.0, 16093.0, 183.0, 117.0, 10129.0, 0.005741130701079948, 0.0031661684465465866, 0.305, 0.0, 10.0, 44.0, 74.0, 1.0, 51.0, 357.4, 7.777777777777778, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.22755417956656346, 15.849587203302374, 1.0, 1.0, 1.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(65.46128985748196, 34.53871014251805)) 2017-05-06T01:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.65949043705868, 0.34050956294132)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.52, 45.0, 216.0, 0.11, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 41.0, 22000.0, 16093.0, 167.0, 117.0, 10095.0, 0.005741130701079948, 0.0031661684465465866, 0.384, 0.0, 0.0, 44.0, 74.0, 1.0, 41.0, 346.57, 15.28888888888889, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.22755417956656346, 15.849587203302374, 1.0, 1.0, 1.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(65.94904370586801, 34.050956294132)) 2017-05-07T01:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6019943093507302, 0.3980056906492699)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.36, 46.0, 210.0, 0.28, 1.0, 0.0, 0.0, 113.0, 0.0, 0.0, 0.0, 0.0, 51.0, 22000.0, 16093.0, 150.0, 50.0, 10075.0, 0.005741130701079948, 0.0031661684465465866, 0.264, 0.0, 0.0, 44.0, 74.0, 1.0, 58.0, 337.43, 18.41304347826087, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.22755417956656346, 15.849587203302374, 1.0, 1.0, 1.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(60.19943093507302, 39.80056906492699)) 2017-05-08T01:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6886349455286539, 0.31136505447134616)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.2, 47.0, 218.0, 0.15, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 15.0, 22000.0, 16093.0, 139.0, 106.0, 10115.0, 0.005741130701079948, 0.0031661684465465866, 0.241, 0.0, 0.0, 44.0, 74.0, 1.0, 42.0, 384.16, 9.297872340425531, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.22755417956656346, 15.849587203302374, 1.0, 1.0, 1.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(68.8634

In [0]:
analysis_df_2 = RFwithPredictionDf(3, train2_custom_april7, holdout2_custom_april7, selected_features_tier1_2, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

Random Forest, maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345

In [0]:
display(analysis_df_2)

DATE label probability prediction features rawPrediction 2018-07-01T12:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7218759416618024, 0.27812405833819775)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.4, 46.0, 24.0, 0.11, 0.0, 0.0, 1.0, 0.0, 81.0, 1.0, 0.0, 1.0, 21.0, 1128.0, 9656.0, 239.0, 233.0, 10135.0, 0.004084295979598595, 0.003911492514539067, 0.122, 0.11, 5.931818181818182, 63.0, 65.0, 1.0, 700.0, 529.56, 5.931818181818182, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(72.18759416618023, 27.812405833819774)) 2018-07-05T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.2923377305863185, 0.7076622694136815)) 1.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 1.0, 25.0, 0.0, 0.0, 0.0, 0.21, 45.0, 24.0, 0.05, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 256.0, 233.0, 10247.0, 0.004084295979598595, 0.003911492514539067, 0.089, 0.05, 5.027027027027027, 63.0, 65.0, 1.0, 608.0, 831.45, 5.027027027027027, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(29.233773058631858, 70.76622694136817)) 2018-07-08T12:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6892813389485323, 0.31071866105146767)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.28, 50.0, 24.0, 0.15, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 233.0, 183.0, 10210.0, 0.004084295979598595, 0.003911492514539067, 0.111, 0.15, 12.804347826086957, 63.0, 65.0, 1.0, 625.0, 268.81, 12.804347826086957, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(68.92813389485322, 31.071866105146764)) 2018-07-12T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6649131876189771, 0.33508681238102284)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 10.0, 0.0, 0.0, 0.0, 0.2, 48.0, 24.0, 0.14, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 26.0, 22000.0, 16093.0, 278.0, 228.0, 10176.0, 0.004084295979598595, 0.003911492514539067, 0.109, 0.14, 21.92156862745098, 63.0, 65.0, 1.0, 3544.0, 456.63, 21.92156862745098, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(66.49131876189769, 33.50868123810228)) 2018-07-15T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6941408876940678, 0.3058591123059321)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.27, 49.0, 23.0, 0.2, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3658.0, 16093.0, 256.0, 239.0, 10159.0, 0.004084295979598595, 0.003911492514539067, 0.118, 0.2, 10.555555555555555, 63.0, 65.0, 1.0, 620.0, 2732.33, 10.555555555555555, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(69.41408876940677, 30.585911230593208)) 2018-07-26T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.5812768520052469, 0.4187231479947532)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 11.0, 0.0, 0.0, 0.0, 0.24, 52.0, 24.0, 0.2, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 21.0, 3658.0, 16093.0, 256.0, 189.0, 10166.0, 0.004084295979598595, 0.003911492514539067, 0.184, 0.2, 19.54901960784314, 63.0, 65.0, 1.0, 559.0, 663.54, 19.54901960784314, 0.23773658536585365, 20.26

In [0]:
analysis_df_3 = RFwithPredictionDf(4, train3_custom_april7, holdout3_custom_april7, selected_features_tier1_2, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

Random Forest, maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345

In [0]:
display(analysis_df_3)

DATE label probability prediction features rawPrediction 2018-07-01T12:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6970963872682271, 0.3029036127317728)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.4, 46.0, 24.0, 0.11, 0.0, 0.0, 1.0, 0.0, 81.0, 1.0, 0.0, 1.0, 21.0, 1128.0, 9656.0, 239.0, 233.0, 10135.0, 0.004084295979598595, 0.003911492514539067, 0.122, 0.11, 5.931818181818182, 63.0, 65.0, 1.0, 700.0, 529.56, 5.931818181818182, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(69.70963872682273, 30.29036127317729)) 2018-07-05T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.33867841061623527, 0.6613215893837646)) 1.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 1.0, 25.0, 0.0, 0.0, 0.0, 0.21, 45.0, 24.0, 0.05, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 256.0, 233.0, 10247.0, 0.004084295979598595, 0.003911492514539067, 0.089, 0.05, 5.027027027027027, 63.0, 65.0, 1.0, 608.0, 831.45, 5.027027027027027, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(33.86784106162353, 66.13215893837646)) 2018-07-08T12:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7034406549557468, 0.2965593450442532)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.28, 50.0, 24.0, 0.15, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 233.0, 183.0, 10210.0, 0.004084295979598595, 0.003911492514539067, 0.111, 0.15, 12.804347826086957, 63.0, 65.0, 1.0, 625.0, 268.81, 12.804347826086957, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(70.34406549557468, 29.65593450442532)) 2018-07-12T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6704644021907298, 0.3295355978092703)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 10.0, 0.0, 0.0, 0.0, 0.2, 48.0, 24.0, 0.14, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 26.0, 22000.0, 16093.0, 278.0, 228.0, 10176.0, 0.004084295979598595, 0.003911492514539067, 0.109, 0.14, 21.92156862745098, 63.0, 65.0, 1.0, 3544.0, 456.63, 21.92156862745098, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(67.04644021907298, 32.95355978092703)) 2018-07-15T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.7019115826894099, 0.2980884173105902)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.27, 49.0, 23.0, 0.2, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3658.0, 16093.0, 256.0, 239.0, 10159.0, 0.004084295979598595, 0.003911492514539067, 0.118, 0.2, 10.555555555555555, 63.0, 65.0, 1.0, 620.0, 2732.33, 10.555555555555555, 0.23773658536585365, 20.26208780487805, 4.0, 2.0, 0.18447955390334572, 14.615473977695167, 0.3333333333333333, 1.0, 247.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(70.19115826894097, 29.80884173105901)) 2018-07-26T12:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6180460333899529, 0.3819539666100471)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(961.0, 677.0, 11.0, 0.0, 11.0, 0.0, 0.0, 0.0, 0.24, 52.0, 24.0, 0.2, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 21.0, 3658.0, 16093.0, 256.0, 189.0, 10166.0, 0.004084295979598595, 0.003911492514539067, 0.184, 0.2, 19.54901960784314, 63.0, 65.0, 1.0, 559.0, 663.54, 19.54901960784314, 0.23773658536585365, 20.26208780

In [0]:
analysis_df_4 = RFwithPredictionDf(5, train4_custom_april7, holdout4_custom_april7, selected_features_tier1_2, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

Random Forest, maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345

In [0]:
display(analysis_df_4)

DATE label probability prediction features rawPrediction 2017-07-01T01:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.43586575179168796, 0.5641342482083119)) 1.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 1.0, 19.0, 0.0, 14.0, 1.0, 0.4, 44.0, 234.0, 0.34, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 46.0, 22000.0, 14484.0, 217.0, 144.0, 10105.0, 0.005741130701079948, 0.0031661684465465866, 0.415, 0.0, 0.0, 44.0, 74.0, 1.0, 137.0, 332.72, 16.25, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.22755417956656346, 15.849587203302374, 1.0, 1.0, 1.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(43.5865751791688, 56.413424820831196)) 2017-07-01T00:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6202384994514922, 0.3797615005485078)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(3724.0, 47.0, 607.0, 1.0, 45.0, 1.0, 34.0, 1.0, 0.23, 44.0, 558.0, 0.12, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 62.0, 1829.0, 16093.0, 278.0, 183.0, 10139.0, 0.0030382137378516037, 0.0030766596012927897, 0.377, 0.0, 0.0, 77.0, 77.0, 1.0, 192.0, 352.26, 3.255813953488372, 0.14733161229758274, 9.95539544707815, 11.0, 10.0, 0.15216010165184243, 11.334498094027953, 0.2413793103448276, 1.0, 555.0, 11.0)) Map(vectorType -> dense, length -> 2, values -> List(62.02384994514921, 37.97615005485077)) 2017-07-01T00:00:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6316435227889303, 0.3683564772110697)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2018.0, 13.0, 152.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.2, 523.0, 70.0, 0.37, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 77.0, 22000.0, 16000.0, 178.0, 106.0, 10147.059683313033, 0.022199505825753987, 0.023791018713229747, 0.423, 0.0, 3.0, 7.0, 7.0, 1.0, 92.0, 292.85, 23.237735849056605, 0.19196421625826526, 14.418615324776352, 7.0, 7.0, 0.2642515630746598, 19.1789523459255, 0.6666666666666666, 1.0, 3.0, 16.0)) Map(vectorType -> dense, length -> 2, values -> List(63.16435227889302, 36.83564772110696)) 2017-07-01T02:53:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7212108533836816, 0.27878914661631843)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2519.0, 152.0, 841.0, 0.0, 9.0, 0.0, 0.0, 0.0, 0.21, 68.0, 428.0, 0.07, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 31.0, 2134.0, 14484.0, 167.0, 89.0, 10091.0, 0.007422320923543924, 0.008996132956866196, 0.45, 0.0, 0.0, 32.0, 26.0, 1.0, 57.0, 316.58, 4.676470588235294, 0.14858309931069696, 11.147821934776237, 10.0, 8.0, 0.10628439038517232, 7.897770055024616, 0.16666666666666666, 1.0, 1382.0, 45.0)) Map(vectorType -> dense, length -> 2, values -> List(72.12108533836816, 27.878914661631843)) 2017-07-01T00:00:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.5824582606829277, 0.4175417393170722)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(212.0, 312.0, 18.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.19, 118.0, 321.0, 0.13, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 67.0, 22000.0, 16000.0, 289.0, 200.0, 10118.769849246231, 0.005007078184149604, 0.006047857003368609, 0.317, 0.5, 49.0, 50.0, 42.0, 1.0, 70.0, 421.22, 9.025423728813559, 0.19196421625826526, 14.418615324776352, 7.0, 7.0, 0.15122016268835844, 11.976930257367648, 0.43956043956043955, 1.0, 42.0, 49.0)) Map(vectorType -> dense, length -> 2, values -> List(58.2458260682928, 41.75417393170724)) 2017-07-01T03:53:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.4697940821807957, 0.5302059178192043)) 1.0 Map(vectorType -> dense, length -> 47, values -> List(2569.0, 62.0, 13.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.41, 146.0, 257.0, 0.26, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 36.0, 22000.0, 16093.0, 167.0, 122.0, 10139.0, 0.006353225529933073, 0.005475389132165931, 0.32, 1.0, 120.0, 40.0, 45.0, 1.0, 1820.0, 523.95, 12.876712328767123, 0.25462412275484714, 17.62190733912216, 2.0, 3.0, 0.20992867867867868, 12.217905405405405, 0.483870967741935

In [0]:
analysis_df_0.write.parquet(f"{blob_url}/RF_pred_table_cvgroup0_0410")
analysis_df_1.write.parquet(f"{blob_url}/RF_pred_table_cvgroup1_0410")
analysis_df_2.write.parquet(f"{blob_url}/RF_pred_table_cvgroup2_0410")
analysis_df_3.write.parquet(f"{blob_url}/RF_pred_table_cvgroup3_0410")
analysis_df_4.write.parquet(f"{blob_url}/RF_pred_table_cvgroup4_0410")


In [0]:
df = spark.read.parquet(f"{blob_url}/RF_pred_table_cvgroup0_0410")
display(df)

DATE label probability prediction features rawPrediction 2016-07-02T18:00:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6438436287878243, 0.35615637121217575)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(2327.0, 60.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.52, 27.0, 202.0, 0.15, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 31.0, 11524.85510428101, 16000.0, 211.0, 144.0, 10135.871569703622, 0.003500544675913835, 0.0027747531201398517, 0.241, 0.15, 9.029411764705882, 66.0, 82.0, 0.0, 64.0, 330.3, 9.029411764705882, 0.2174832779656472, 14.362938906848212, 3.0, 2.0, 0.15740380878352117, 9.674698795180722, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(64.38436287878241, 35.61563712121757)) 2016-07-03T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7737283299801707, 0.22627167001982929)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 1.0, 60.0, 1.0, 56.0, 1.0, 0.18, 18.0, 291.0, 0.05, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 110.0, 30.0, 10213.0, 0.0026349144472628, 0.0025650351982225914, 0.084, 0.05, 4.35, 81.0, 87.0, 1.0, 610.0, 481.47, 4.35, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(77.37283299801706, 22.627167001982926)) 2016-07-05T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7451930279798183, 0.25480697202018165)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.1, 18.0, 391.0, 0.29, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 110.0, 30.0, 10186.0, 0.0026349144472628, 0.0025650351982225914, 0.078, 0.29, 27.142857142857142, 81.0, 87.0, 1.0, 681.0, 697.89, 27.142857142857142, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(74.51930279798184, 25.480697202018167)) 2016-07-06T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8008263388860298, 0.19917366111397017)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.17, 18.0, 392.0, 0.11, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 15.0, 3353.0, 16093.0, 80.0, 30.0, 10173.0, 0.0026349144472628, 0.0025650351982225914, 0.11, 0.0, 0.0, 81.0, 87.0, 1.0, 681.0, 438.94, 4.833333333333333, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(80.08263388860301, 19.917366111397026)) 2016-07-07T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7619175131735116, 0.23808248682648833)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.22, 17.0, 391.0, 0.22, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 26.0, 22000.0, 16093.0, 20.0, -10.0, 10196.0, 0.0026349144472628, 0.0025650351982225914, 0.134, 0.0, 0.0, 81.0, 87.0, 1.0, 669.0, 820.54, 6.444444444444445, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333333333333333, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(76.19175131735118, 23.808248682648838)) 2016-07-08T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8022482292200129, 0.19775177077998712)) 0.0 Map(vectorType -> dense, length -> 47, values -> List(1265.0, 6451.0, 97.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.24, 17.0, 392.0, 0.06, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 22000.0, 16093.0, 40.0, 10.0, 10217.0, 0.0026349144472628, 0.0025650351982225914, 0.094, 0.0, 0.0, 81.0, 87.0, 1.0, 674.0, 406.17, 4.352941176470588, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.3333

In [0]:
metrics_0 = MulticlassMetrics(analysis_df_0.rdd)
f1_model0 = metrics_0.fMeasure(1.0,1.0)
metrics_1 = MulticlassMetrics(analysis_df_1.rdd)
f1_model1 = metrics_1.fMeasure(1.0,1.0)
metrics_2 = MulticlassMetrics(analysis_df_2.rdd)
f1_model2 = metrics_2.fMeasure(1.0,1.0)
metrics_3 = MulticlassMetrics(analysis_df_3.rdd)
f1_model3 = metrics_3.fMeasure(1.0,1.0)
metrics_4 = MulticlassMetrics(analysis_df_4.rdd)
f1_model4 = metrics_4.fMeasure(1.0,1.0)

In [0]:
print(f'f1_model0: {f1_model0}')
print(f'f1_model1: {f1_model1}')
print(f'f1_model2: {f1_model2}')
print(f'f1_model3: {f1_model3}')
print(f'f1_model4: {f1_model4}')

### Check the collinearity of the Tier1 + Tier2 features

In [0]:
# selected features

# tier 1 (criteria of 1 > 0.005)
selected_features_tier1 = 

print(f'selected_features_tier1: {len(selected_features_tier1)}')
print(f'{selected_features_tier1}')

# tier 1 + 2 (criteria of 2 > 0.0001)
selected_features_tier1_2 = 

print(f'selected_features_tier1 & 2: {len(selected_features_tier1_2)}')
print(f'{selected_features_tier1_2}')

# original features
print(f'feature_list_full_0: {len(feature_list_full_0)}')
print(f'{feature_list_full_0}')

df_5yr_join_cv_april7

In [0]:
from pyspark.mllib.stat import Statistics
from pyspark.ml.stat import Correlation

selected_features_tier1_A = ['DEP_DEL15', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW']#, 'prior_arr_delayed']#, 'previous_ARR_DELAY_NEW']        
selected_features_tier1_B = ['DEP_DEL15', 'plane_is_here', 'avg_carrier_delay_24hrs', 'avg_ori_airport_delay_24hrs','evening']
selected_features_tier1_C = ['DEP_DEL15', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'time_inb_flight_min','avg_ori_DEP_DELAY_NEW_24hr']

corr_df = df_5yr_join_cv_april7.select(selected_features_tier1_A)
# corr_df_B = df_5yr_join_cv_april7.select(selected_features_tier1_B)

col_names = corr_df.columns
features = corr_df.rdd.map(lambda row:row[0:])
corr_mat = Statistics.corr(features, method='pearson')
corr_df = pd.DataFrame(corr_mat)
corr_df.index, corr_df.columns = col_names, col_names
corr_df

### Sample result: Simple run with 10 features as of April 5

# 5. Threshold optimization in RF

Reference: [Difference between raw prediction and probability](https://stackoverflow.com/questions/37903288/what-do-columns-rawprediction-and-probability-of-dataframe-mean-in-spark-mll)

In [0]:
print(len(train0_custom_april7.columns))
print(len(holdout0_custom_april7.columns))

# analysis_df_1
# analysis_df_2
# analysis_df_3
# analysis_df_4
# analysis_df_5

feature_list = selected_features_tier1_2
train = train0_custom_april7 # 20150101-20151231
holdout = holdout0_custom_april7 # 20160101-20161231
maxDepth=8
maxBins=64
minInstancesPerNode=10
numTrees=100
seed=12345
rebalance_input_tup=(True, 1.6)
verbose=0
CV_group=1

## 5-1. Define Function for Threhold Optimization

### Add Columns that contains P(class=0), P(class=1)

In [0]:
# display(analysis_df.withColumn('prob_0',col('probability')['values']))
from pyspark.sql.functions import udf, col
from pyspark.sql.types import FloatType, DoubleType, IntegerType, StringType

def extract_prob_0(x):
    try:
        return float(x[0])  # Your VectorUDT is of length 2
    except ValueError:
        return None
      
def extract_prob_1(x):
    try:
        return float(x[1])  # Your VectorUDT is of length 2
    except ValueError:
        return None

extract_prob_0_udf = udf(extract_prob_0, DoubleType())
extract_prob_1_udf = udf(extract_prob_1, DoubleType())

### Define function that apply chosen threshold to final modeling. Returns table of prediction

In [0]:
# function that creates the column with P(class=0) and P(class=1)

from pyspark.sql.functions import udf, col
from pyspark.sql.types import FloatType, DoubleType, IntegerType, StringType

def extract_prob_0(x):
    try:
        return float(x[0])  # Your VectorUDT is of length 2
    except ValueError:
        return None

extract_prob_0_udf = udf(extract_prob_0, DoubleType())
########################################################################################
def extract_prob_1(x):
    try:
        return float(x[1])  # Your VectorUDT is of length 2
    except ValueError:
        return None

extract_prob_1_udf = udf(extract_prob_1, DoubleType())
########################################################################################

In [0]:
# define functions that returns 1 or 0 based on the probability and threshold 
def pred_by_threshold(x): #x: prob_1
  global threshold
  try:
    if x >= threshold:
      return int(1)
    elif x < threshold:
      return int(0)
  except ValueError:
      return None
pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())
########################################################################################

# define functions that returns TP/FP/FN/TN based on the prediction in each threshold 
def evalPred(pred, true):
  if pred == 1:
    if true == 1:
      return 'TP'
    elif true == 0:
      return 'FP'
  elif pred == 0:
    if true == 1:
      return 'FN'
    elif true == 0:
      return 'TN'
udf_evalPred = udf(lambda x,y:evalPred(x,y), StringType()) 

########################################################################################

# Based on the dataframe with prob_1 and prob_0, convert the spark df to pandas df with TP/TN/FP/FN, calculate f1 score and returns the df of the result
def f1Eval(idx, threshold):

  global f1_by_threshold, analysis_df_th, best_f1_score
  
  # add column of prediction 
  analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
  # add evaluation column     
  analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label')) 
  
  # gain a result
  result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
  pdf_result = result.toPandas()
  print(pdf_result)
  
  # count TP/FP/FN and return zero if denominator/numerator of f1 is zero
  if "TP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    print('NO TP')
    f1_score = 0
  elif "FP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    if "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
      FN, FP = 0, 0
      print('NO FN FP')
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      f1_score = 2*TP/(2*TP+FN+FP)
    else:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      FP = 0
      print('NO FP')
      f1_score = 2*TP/(2*TP+FN+FP)
  elif "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = 0
    f1_score = 2*TP/(2*TP+FN+FP)
  else:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]      
    f1_score = 2*TP/(2*TP+FN+FP)
  
  f1_by_threshold += [[idx,threshold,f1_score]]
   
  if f1_score > best_f1_score:
    best_f1_score = f1_score
  print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best f1 score: {best_f1_score}')
  
  return f1_by_threshold, analysis_df_th
########################################################################################

In [0]:
#Add column
analysis_df_th = analysis_df_0.withColumn("prob_0", extract_prob_0_udf(col("probability")))\
                           .withColumn("prob_1", extract_prob_1_udf(col("probability")))

search_space = np.linspace(0.05, 0.95, 50)
f1_by_threshold = [['index','threshold','f1_score']]

best_f1_score = 0
best_f1_index = 0

for idx, threshold in enumerate(search_space):
  f1_by_threshold_0, analysis_df_th_0 = f1Eval(idx, threshold)

In [0]:
# Based on the dataframe with prob_1 and prob_0, convert the spark df to pandas df with TP/TN/FP/FN, calculate f1 score and returns the df of the result
def f1_Eval(search_space, analysis_df):

  f1_by_threshold = [['index','threshold','f1_score']]
  best_f1_score = 0
  best_f1_index = 0
  best_threshold = 0
  
  analysis_df_th = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))
  
  for idx, threshold in enumerate(search_space):
    #global f1_by_threshold, analysis_df_th, best_f1_score
    
    # add column of prediction 
    analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
    # add evaluation column     
    analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label')) 
    display(analysis_df_th)

    # gain a result
    result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
    pdf_result = result.toPandas()
    print(pdf_result)

    TPTNFPFN_list = [i for i in pdf_result["eval_"+str(idx)]]
    if "TP" in TPTNFPFN_list:
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    elif "TP" not in TPTNFPFN_list:
      TP = 0
    if "TN" in TPTNFPFN_list:
      TN = list(pdf_result[pdf_result["eval_"+str(idx)]=='TN']['count'])[0]
    elif "TN" not in TPTNFPFN_list:
      TN = 0
    if "FP" in TPTNFPFN_list:
      FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    elif "FP" not in TPTNFPFN_list:
      FP = 0
    if "FN" in TPTNFPFN_list:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
    elif "FN" not in TPTNFPFN_list:
      FN = 0

    # count TP/FP/FN and return zero if denominator/numerator of f1 is zero
    if 2*TP+FN+FP == 0:
      f1_score = 0
    elif 2*TP+FN+FP != 0:
      f1_score = 2*TP/(2*TP+FN+FP)

    f1_by_threshold += [[idx,threshold,f1_score]]

    if f1_score > best_f1_score:
      best_f1_score = f1_score
      best_f1_index = idx
      best_threshold = threshold
    print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best_f1_index: {best_f1_index}, best_threshold: {best_threshold }, best f1 score: {best_f1_score}')

  return f1_by_threshold, analysis_df_th, best_f1_score, best_f1_index, best_threshold

In [0]:
display(analysis_df_0)

In [0]:
search_space = np.linspace(0.05, 0.95, 50)
print(f'cv_group_0')
f1_by_threshold_0, analysis_df_th_0, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_0)
f1_by_threshold_0

In [0]:
analysis_df_th_0

In [0]:
print(f'cv_group_1')
f1_by_threshold_1, analysis_df_th_1, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_th_1)
print(f'cv_group_2')
f1_by_threshold_2, analysis_df_th_2, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_th_2)
print(f'cv_group_3')
f1_by_threshold_3, analysis_df_th_3, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_th_3)
print(f'cv_group_4')
f1_by_threshold_4, analysis_df_th_4, best_f1_score, best_f1_index, best_threshold  = f1_Eval(search_space, analysis_df_th_4)


In [0]:
CV_group_num = 1

def FinalTestWithBestThreshold(CV_group_num, trainAll, test, feature_list, threshold, maxDepth=5, maxBins=16, minInstancesPerNode=10, numTrees=100, seed=12345):
  # Assemble features
  assembler = VectorAssembler().setInputCols(feature_list)\
                            .setOutputCol('features')

  assmb_train = assembler.transform(trainAll)
  assmb_holdout = assembler.transform(test)

  # modeling
  rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                              maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed)
  rfModel = rf.fit(assmb_train)
  predictions = rfModel.transform(assmb_holdout)

  # predictions.select('DEP_DEL15','normalized_features')
  results = predictions.select(['prediction', 'DEP_DEL15'])
  results = results.withColumnRenamed('DEP_DEL15', 'label')
  # display(results.head(5))
  metrics = MulticlassMetrics(results.rdd)
  
  # gain prediction df and separate probability vector
  feature_for_analysis = ['DATE','DEP_DEL15','probability','prediction','features', 'rawPrediction']
  analysis_df = predictions.select(feature_for_analysis)
  
  extract_prob_0_udf = udf(extract_prob_0, DoubleType())
  extract_prob_1_udf = udf(extract_prob_1, DoubleType())
  analysis_df = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))
  
  # based on the defined threshold, create vector of prediction
  # add column of prediction 
  analysis_df = analysis_df.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
  # add evaluation column     
  analysis_df = analysis_df.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'DEP_DEL15')) 
  
  # show prediction of the single model
  analysis_df_th = analysis_df
  f1_by_threshold = [['index','threshold','f1_score']]
  best_f1_score = 0
  best_f1_index = 0
  print(f'CV_group_num: {CV_group_num}#############################################################################')
  f1_by_threshold, analysis_df_th = f1Eval(CV_group_num, threshold)
  
  return analysis_df


In [0]:
analysis_df = FinalTestWithBestThreshold(CV_group_num, trainAll_april7, test_april7, feature_list, threshold=0.5, maxDepth=5, maxBins=16, minInstancesPerNode=10, numTrees=100, seed=12345)

### Quick hyperparameter tuning with 3years + 1years data work first optimization with all the five CV groups

## Write function that add column of predictions & evaluations of each threshold

In [0]:
search_space = np.linspace(0.05, 0.95, 50)
analysis_df_th = analysis_df_2

f1_by_threshold = [['index','threshold','f1_score']]
best_f1_score = 0
best_f1_index = 0

for idx, threshold in enumerate(search_space):
  
  # define functions that returns 1 or 0 based on the probability and threshold 
  def pred_by_threshold(x): #x: prob_1
    global threshold
    try:
      if x >= threshold:
        return int(1)
      elif x < threshold:
        return int(0)
    except ValueError:
        return None
  pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())
  
  # add column of prediction 
  analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
  
  # define functions that returns TP/FP/FN/TN based on the prediction in each threshold 
  def evalPred(pred, true):
    if pred == 1:
      if true == 1:
        return 'TP'
      elif true == 0:
        return 'FP'
    elif pred == 0:
      if true == 1:
        return 'FN'
      elif true == 0:
        return 'TN'

  # add evaluation column   
  udf_evalPred = udf(lambda x,y:evalPred(x,y), StringType()) 
  analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'DEP_DEL15')) 
  
  # gain a result
  result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
  pdf_result = result.toPandas()
  print(pdf_result)
  if "TP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    print('NO TP')
    f1_score = 0
  elif "FP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    if "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
      FN, FP = 0, 0
      print('NO FN FP')
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      f1_score = 2*TP/(2*TP+FN+FP)
    else:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      FP = 0
      print('NO FP')
      f1_score = 2*TP/(2*TP+FN+FP)
  elif "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = 0
    f1_score = 2*TP/(2*TP+FN+FP)
  else:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]      
    f1_score = 2*TP/(2*TP+FN+FP)
  
  f1_by_threshold += [[idx,threshold,f1_score]]
   
  if f1_score > best_f1_score:
    best_f1_score = f1_score
    best_f1_index = idx
  print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best f1 index: {best_f1_index}, best f1 score: {best_f1_score}')

In [0]:
f1_by_threshold

## APPENDIX  Single run of random search with hyperopt

https://docs.databricks.com/_static/notebooks/hyperopt-spark-ml.html

https://docs.databricks.com/applications/machine-learning/automl-hyperparam-tuning/hyperopt-concepts.html

# 4. Tune models with hyperopt

In [0]:
from sklearn.datasets import fetch_openml
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.utils import check_random_state

from hyperopt import fmin, hp, tpe
from hyperopt import SparkTrials, STATUS_OK, Trials
from hyperopt.pyll import scope
import hyperopt

## 4-1. Define list/df to store the records of tuning

In [0]:
# df
cv_group_list = [[train0_custom_april7, holdout0_custom_april7],
                 [train1_custom_april7, holdout1_custom_april7],
                 [train2_custom_april7, holdout2_custom_april7],
                 [train3_custom_april7, holdout3_custom_april7],
                 [train4_custom_april7, holdout4_custom_april7]]

# tier 1 + 2 (criteria of 2 > 0.0001)
selected_features_tier1_2 = ['ORI_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'pacific_islands', 'summer', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_thunderstorm', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp','depDelayPageRank', 'arrDelayPageRank', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min','avg_ori_DEP_DELAY_NEW_24hr']
feature_list = selected_features_tier1_2


# hyper parameter list that we want to store the records
# align the parameters that you are setting in the "search space"
parameter_dict = {'maxDepth':[],'maxBins':[],'numTrees':[],'minInstancesPerNode':[]}

# store cv result for each cv group
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

# store best parameter in each cv group
best_hyperparameters_df = pd.DataFrame()

## 4-1. Define list/df to store the records of tuning

In [0]:
# df
cv_group_list = [[train0_custom_april7, holdout0_custom_april7],
                 [train1_custom_april7, holdout1_custom_april7],
                 [train2_custom_april7, holdout2_custom_april7],
                 [train3_custom_april7, holdout3_custom_april7],
            p     [train4_custom_april7, holdout4_custom_april7]]

# tier 1 + 2 (criteria of 2 > 0.0001)
selected_features_tier1_2 = ['ORI_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'pacific_islands', 'summer', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_thunderstorm', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp','depDelayPageRank', 'arrDelayPageRank', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min','avg_ori_DEP_DELAY_NEW_24hr']
feature_list = selected_features_tier1_2


# hyper parameter list that we want to store the records
# align the parameters that you are setting in the "search space"
parameter_dict = {'maxDepth':[],'maxBins':[],'numTrees':[],'minInstancesPerNode':[]}

# store cv result for each cv group
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

# store best parameter in each cv group
best_hyperparameters_df = pd.DataFrame()

## Option. Create a flow for logging
- Not necessary but nice to have

In [0]:
import mlflow
# As explained in Cmd 2 of this notebook, MLflow autologging for `pyspark.ml` requires MLflow version 1.17.0 or above.
# This try-except logic allows the notebook to run with older versions of MLflow.
try:
  import mlflow.pyspark.ml
  mlflow.pyspark.ml.autolog()
except:
  print(f"Your version of MLflow ({mlflow.__version__}) does not support pyspark.ml for autologging. To use autologging, upgrade your MLflow client version or use Databricks Runtime for ML 8.3 or above.")

## 4-2. Define function to train a model
- Define a function that trains the model
- Wrapping the training code in a function is important for passing the function to Hyperopt for tuning later.

In [0]:
def train_RF(params, train, holdout):
  """
  main training function which we pass to Hyperopt.
  It takes in hyperparameter settings, fits a model based on those settings,
  evaluates the model, and returns the loss.

  :param params: map specifying the hyperparameter settings to test
  :return: loss for the fitted model
  """
  
  global cv_result, CV_group_num
  
  # change "DEP_DEL15" to "label"
  train = train.withColumnRenamed("DEP_DEL15","label")
  holdout = holdout.withColumnRenamed("DEP_DEL15","label")
  
  with mlflow.start_run(nested=True):
    # modeling
    rf = RandomForestClassifier()
    
    # params contains the dictionary of randomly picked hyper parameters
    # we need to assign hyper parameters in the params to model
    
    # print parameters that we are assigning to the model
    print(f'CV_group: {CV_group_num}, Parameters: {params}') 
    for k in params.keys():
        # getParam: funtion of RF classifier in pySpark
        p = rf.getParam(k) 
        # model.set(): Assign parameter to the model(funtion of RF classifier in pySpark)
        rf.set(p, params[k])
        
        # add values of each parameter to dictionary
        parameter_dict[k].append(params[k])
    
    # fit the model
    rfModel = rf.fit(train)
    predictions = rfModel.transform(holdout)

    # gain result of the prediction
    results = predictions.select(['prediction', 'label'])
    metrics = MulticlassMetrics(results.rdd)
    f1 = metrics.fMeasure(1.0,1.0)

    #  Update the result and store the record to list/df
    #  cv_result_run = ['CV_group','Accuracy','Recall','Precision','f1_score']
    cv_result_run = [[CV_group_num, metrics.accuracy, metrics.recall(label=1), metrics.precision(1), metrics.fMeasure(1.0,1.0)]]
    cv_result += cv_result_run

    print(f'CV_group: {CV_group_num}, Accuracy: {metrics.accuracy}, Recall: {metrics.recall(label=1)},Precision: {metrics.precision(1)}, F1_score: {metrics.fMeasure(1.0,1.0)}')
  return f1, cv_result

## 4-3. Define search space

In [0]:
# look at Cmd just before the "End of hyperopt" to see the options that we could apply to search space
# WARNING: If we choose "choice", parameters are returned as index. If maxBins = 16 is the best, 0 is returned as value
search_space = {
    'maxDepth': hp.quniform('maxDepth', 3,7,q=1),#,#range(3,10)),
    'maxBins': hp.choice('maxBins',[16,32,64,128]),
    'numTrees': hp.choice('numTrees', [20, 40, 60, 80, 100, 120, 140, 160]),
    'minInstancesPerNode': hp.choice('minInstancesPerNode',[1,10,50,100])
    }

#### Option: Selecting only the features that we are using could be safer to avoid error

## 4-4. Tune the model with hyperopt

### 4-4-1. Tune a single cv group
- If you want to run all the cv groups, go to the next section

In [0]:
CV_group_num = 1
CV_group[0] = train1_
CV_group[1] = holdout1_
best_hyperparameters_df_ = pd.DataFrame()

# for CV_group_num, CV_group in enumerate(cv_group_list):

# Assemble features
assembler_tmp = VectorAssembler().setInputCols(feature_list)\
                          .setOutputCol('features')

assmb_train_tmp = assembler_tmp.transform(CV_group[0])
assmb_holdout_tmp = assembler_tmp.transform(CV_group[1])


# defining hyperopt_f to keep the best f1 score
# 'loss' is the default description in hyperopt. 
  # It is to design to minimize, therefore we need to use -f1 to maximize the value
count = 0
best = 0
def hyperopt_f(params):
  global best, count #, #cv_result, CV_group_num
  count += 1
  f1, cv_result = train_RF(params.copy(),assmb_train_tmp, assmb_holdout_tmp)
  if f1 > best:
    print(f'new best: {f1}')
    best = f1
  if count % 50 == 0:
      print(f'iters: {count}, f1: {f1} using {params}')
  return {'loss': -(f1), 'status': STATUS_OK}

# trials stores the record but we did not use here
trials = Trials()
# fmin is the default function of hyperopt. see official doc for detalils
best_hyperparameters = fmin(fn=hyperopt_f,
                            space=search_space,
                            algo=tpe.suggest, # We have random.tpe.suggest as an option, but tpe.suggest if commonly used in hyperopt
                            max_evals=2, # how many combinations of parameters we would like to try
                            verbose=1)
print(f'CV_group_num: {CV_group_num}, f1: {best}, best_hyperparameters: {best_hyperparameters}')

# update dataframe that stores the result
best_hyperparameters_df = pd.concat([best_hyperparameters_df,pd.DataFrame([best_hyperparameters])], axis=0)
pd.DataFrame([best_hyperparameters]) 

best_hyperparameters_df

In [0]:
cv_result_df = pd.DataFrame(cv_result[1:],columns=cv_result[0])
cv_result_df

In [0]:
best_hyperparameters_df

### 4-4-2 Tune each model of all the CV groups

In [0]:
# CV_group_num = 1
# CV_group[0] = train1_
# CV_group[1] = holdout1_

# align the parameters that you are setting in the "search space"
parameter_dict = {'maxDepth':[],'maxBins':[],'numTrees':[],'minInstancesPerNode':[]}

# store cv result for each cv group
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

feature_list = selected_features_tier1_2

# store best parameter in each cv group
best_hyperparameters_df = pd.DataFrame()

# run for loop across every CV group 
for CV_group_num, CV_group in enumerate(cv_group_list):  
  
  # Assemble features
  assembler_tmp = VectorAssembler().setInputCols(feature_list)\
                            .setOutputCol('features')

  assmb_train_tmp = assembler_tmp.transform(CV_group[0])
  assmb_holdout_tmp = assembler_tmp.transform(CV_group[1])


  # defining hyperopt_f to keep the best f1 score
  # 'loss' is the default description in hyperopt. 
    # It is to design to minimize, therefore we need to use -f1 to maximize the value
  count = 0
  best = 0
  def hyperopt_f(params):
    
    global best, count #, #cv_result, CV_group_num
    count += 1
    f1, cv_result = train_RF(params.copy(),assmb_train_tmp, assmb_holdout_tmp)
    if f1 > best:
      print(f'new best: {f1}')
      best = f1
    if count % 50 == 0:
        print(f'iters: {count}, f1: {f1} using {params}')
    return {'loss': -(f1), 'status': STATUS_OK}

  # trials stores the record but we did not use here
  trials = Trials()
  # fmin is the default function of hyperopt. see official doc for detalils
  best_hyperparameters = fmin(fn=hyperopt_f,
                              space=search_space,
                              algo=tpe.suggest, # We have random.tpe.suggest as an option, but tpe.suggest if commonly used in hyperopt
                              max_evals=2, # how many combinations of parameters we would like to try
                              verbose=1)
  print(f'CV_group_num: {CV_group_num}, f1: {best}, best_hyperparameters: {best_hyperparameters}')

  # update dataframe that stores the result
  best_hyperparameters_df = pd.concat([best_hyperparameters_df,pd.DataFrame([best_hyperparameters])], axis=0)
  pd.DataFrame([best_hyperparameters]) 

best_hyperparameters_df

In [0]:
cv_group_list = [[train_3yrs, holdout_1yr]]#[train0, holdout0],[train1, holdout1],[train2,holdout2],
#                  [train3, holdout3],[train4, holdout4],[train5,holdout5],
#                  [train6, holdout6],[train7, holdout7],[train8,holdout8]]

# cv result for each cv group
cv_result = [['CV_group','Accuracy','Recall','Precision','f1_score']]

# best parameter in each cv group
best_hyperparameters_df = pd.DataFrame()


In [0]:
for CV_group_num, CV_group in enumerate(cv_group_list):
  # Assemble features
  assembler_tmp = VectorAssembler().setInputCols(feature_list)\
                            .setOutputCol('features')

  assmb_train_tmp = assembler_tmp.transform(CV_group[0])
  assmb_holdout_tmp = assembler_tmp.transform(CV_group[1])

  count = 0
  best = 0
  def hyperopt_f(params):
    global best, count, cv_result, CV_group_num
    count += 1
    f1, cv_result = train_RF(params.copy(),assmb_train_tmp, assmb_holdout_tmp)
    if f1 > best:
      print(f'new best: {f1}')
      best = f1
    if count % 50 == 0:
        print(f'iters: {count}, f1: {f1} using {params}')
    return {'loss': -(f1), 'status': STATUS_OK}

  # We can run Hyperopt locally (only on the driver machine)
  trials = Trials()
  best_hyperparameters = fmin(fn=f,
                              space=search_space,
                              algo=tpe.rand.suggest,
                              max_evals=10,# maximum number of iterations
                              verbose=1)
  print(f'CV_group_num: {CV_group_num}, f1: {best}, best_hyperparameters: {best_hyperparameters}')

  best_hyperparameters_df = pd.concat([best_hyperparameters_df,pd.DataFrame([best_hyperparameters])], axis=0)
  pd.DataFrame([best_hyperparameters]) 

best_hyperparameters_df

## Options for setting search space

`hp.choice(label, options)`

Returns one of the options, which should be a list or tuple. The elements of options can themselves be [nested] stochastic expressions. In this case, the stochastic choices that only appear in some of the options become conditional parameters.

`hp.randint(label, upper)`

Returns a random integer in the range [0, upper). The semantics of this distribution is that there is no more correlation in the loss function between nearby integer values, as compared with more distant integer values. This is an appropriate distribution for describing random seeds for example. If the loss function is probably more correlated for nearby integer values, then you should probably use one of the "quantized" continuous distributions, such as either quniform, qloguniform, qnormal or qlognormal.

`hp.uniform(label, low, high)`

Returns a value uniformly between low and high.
When optimizing, this variable is constrained to a two-sided interval.

`hp.quniform(label, low, high, q)`

Returns a value like round(uniform(low, high) / q) * q
Suitable for a discrete value with respect to which the objective is still somewhat "smooth", but which should be bounded both above and below.

`hp.loguniform(label, low, high)`

Returns a value drawn according to exp(uniform(low, high)) so that the logarithm of the return value is uniformly distributed.
When optimizing, this variable is constrained to the interval [exp(low), exp(high)].

`hp.qloguniform(label, low, high, q)`

Returns a value like round(exp(uniform(low, high)) / q) * q
Suitable for a discrete variable with respect to which the objective is "smooth" and gets smoother with the size of the value, but which should be bounded both above and below.

`hp.normal(label, mu, sigma)`

Returns a real value that's normally-distributed with mean mu and standard deviation sigma. When optimizing, this is an unconstrained variable.

`hp.qnormal(label, mu, sigma, q)`

Returns a value like round(normal(mu, sigma) / q) * q
Suitable for a discrete variable that probably takes a value around mu, but is fundamentally unbounded.

`hp.lognormal(label, mu, sigma)`

Returns a value drawn according to exp(normal(mu, sigma)) so that the logarithm of the return value is normally distributed. When optimizing, this variable is constrained to be positive.

`hp.qlognormal(label, mu, sigma, q)`

Returns a value like round(exp(normal(mu, sigma)) / q) * q
Suitable for a discrete variable with respect to which the objective is smooth and gets smoother with the size of the variable, which is bounded from one side.

In [0]:
RandomForestCV(trainAll, test, feature_list, 
                   maxDepth=4, maxBins=16, minInstancesPerNode=10, numTrees=117, seed=12345, CV_group=1, verbose=0)

# runCV_RandomForest(cv_group_list, feature_list, verbose=0, rebalance_input_tup=(False, 4.545), maxDepth=4, maxBins=16, minInstancesPerNode=10, numTrees=117, seed=12345)

## Predict final test data with "best" params